In [28]:
import os, json, uuid, base64, re
from typing import List, Dict, Tuple, TypedDict, Literal, Optional
from dataclasses import dataclass
from pathlib import Path

import numpy as np
import pandas as pd
import faiss

from pypdf import PdfReader

import pymupdf

# 환경변수 생성하기
from dotenv import load_dotenv
load_dotenv()

# LangGraph
from langgraph.graph import StateGraph, START, END

# 
from openai import OpenAI
client = OpenAI()  # 환경변수 OPENAI_API_KEY 필요

EMBED_MODEL = "text-embedding-3-small"   # 1536차원, 비용 대비 성능 우수
GEN_MODEL   = "gpt-4o-mini"              # 멀티모달(텍스트+이미지) 추론 모델
TOP_K = 10

# 데이터 경로 - 해당부분 
PDF_PATH = "/Users/ijongseung/Energy-RAG/rag/" # 
PDF_NAME = "2024산업부문에너지온실가스실태조사및통계분석보고서.pdf"
DOC_ID   = "energy_usage_2017"

In [29]:
def split_pdf(filepath, batch_size=10):
    """
    입력 PDF를 여러 개의 작은 PDF 파일로 분할
    """
    # PDF 파일 열기
    input_pdf = pymupdf.open(filepath)
    num_pages = len(input_pdf)
    print(f"총 페이지 수: {num_pages}")

    ret = []
    # PDF 분할
    for start_page in range(0, num_pages, batch_size):
        end_page = min(start_page + batch_size, num_pages) - 1

        # 분할된 PDF 저장
        input_file_basename = os.path.splitext(filepath)[0]
        output_file = f"{input_file_basename}_{start_page:04d}_{end_page:04d}.pdf"
        print(f"분할 PDF 생성: {output_file}")

        with pymupdf.open() as output_pdf:
            output_pdf.insert_pdf(input_pdf, from_page=start_page, to_page=end_page)
            output_pdf.save(output_file)
            ret.append(output_file)

    # 입력 PDF 파일 닫기
    input_pdf.close()
    return ret

In [33]:
import os
import json
import requests
import pymupdf

class LayoutAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key

    def _upstage_layout_analysis(self, input_file):
        """
        레이아웃 분석 API 호출 후 결과 JSON 저장
        """
        response = requests.post(
            "https://api.upstage.ai/v1/document-ai/layout-analysis",
            headers={"Authorization": f"Bearer {self.api_key}"},
            data={"ocr": False},
            files={"document": open(input_file, "rb")},
        )

        if response.status_code == 200:
            output_file = os.path.splitext(input_file)[0] + ".json"
            with open(output_file, "w", encoding="utf-8") as f:
                json.dump(response.json(), f, ensure_ascii=False, indent=2)
            return output_file
        else:
            raise ValueError(f"예상치 못한 상태 코드: {response.status_code}")

    def execute(self, input_file):
        return self._upstage_layout_analysis(input_file)


def split_pdf(filepath, batch_size=10, output_dir=None):
    """
    PDF를 batch_size 단위로 분할 저장 (output_dir 지정 가능)
    """
    input_pdf = pymupdf.open(filepath)
    num_pages = len(input_pdf)
    print(f"총 페이지 수: {num_pages}")

    if output_dir is None:
        output_dir = os.path.dirname(filepath)  # 기본: 원본 PDF와 같은 폴더
    os.makedirs(output_dir, exist_ok=True)

    ret = []
    for start_page in range(0, num_pages, batch_size):
        end_page = min(start_page + batch_size, num_pages) - 1

        base_name = os.path.splitext(os.path.basename(filepath))[0]
        output_file = os.path.join(
            output_dir, f"{base_name}_{start_page:04d}_{end_page:04d}.pdf"
        )
        print(f"분할 PDF 생성: {output_file}")

        with pymupdf.open() as output_pdf:
            output_pdf.insert_pdf(input_pdf, from_page=start_page, to_page=end_page)
            output_pdf.save(output_file)
            ret.append(output_file)

    input_pdf.close()
    return ret


def analyze_pdf(filepath, api_key, batch_size=10, output_dir=None):
    """
    PDF를 분할 → 각 조각별 레이아웃 분석 실행 → JSON 파일 리스트 반환
    """
    analyzer = LayoutAnalyzer(api_key)
    split_files = split_pdf(filepath, batch_size=batch_size, output_dir=output_dir)

    analyzed_files = []
    for pdf_file in split_files:
        result_json = analyzer.execute(pdf_file)
        analyzed_files.append(result_json)

    return analyzed_files


# 실행 예시
if __name__ == "__main__":
    
    api_key = "up_RTdQLb3lzo7lx0CJZ1jnXOQkTCzfh"
    pdf_file = "/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf" # 파일 위치 변경해줘야 함.

    analyzed_files = analyze_pdf(pdf_file, api_key, batch_size=10)
    print(analyzed_files)

총 페이지 수: 238
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0010_0019.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0020_0029.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0030_0039.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0040_0049.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0050_0059.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0060_0069.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0070_0079.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0080_0089.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0090_0099.pdf
분할 PDF 생성: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0100_0109.p

In [36]:
from PIL import Image, ImageDraw

##  cursor 
# 단순하고 효과적인 이미지 추출기 (표 + 그래프 + 텍스트 + 표→Markdown 반영)

class SimpleWorkingExtractor:
    """단순하지만 잘 작동하는 추출기"""
    
    def __init__(self, pdf_file):
        self.pdf_file = pdf_file
    
    def extract_simple(self, json_file, output_dir="simple_output"):
        """단순하지만 효과적인 추출 (텍스트 + 시각요소 + 표→Markdown)"""
        os.makedirs(output_dir, exist_ok=True)
        
        # JSON 로드
        with open(json_file, 'r', encoding='utf-8') as f:
            data = json.load(f)
        
        # 페이지 메타데이터
        meta_pages = {p.get('page'): (p.get('width'), p.get('height'))
                      for p in data.get('metadata', {}).get('pages', [])}
        
        # 파일명에서 페이지 범위 추출
        filename = os.path.basename(json_file)
        if '_' in filename:
            parts = filename.replace('.json', '').split('_')
            if len(parts) >= 3:
                try:
                    start_page = int(parts[-2]) + 1  # 0-based to 1-based
                    end_page = int(parts[-1]) + 1
                except:
                    start_page = 1
            else:
                start_page = 1
        else:
            start_page = 1
        
        # 🔥 시각적 요소 + 텍스트 포함
        elements = data.get('elements', [])
        visual_elements = [e for e in elements if e.get('category') in 
                           ['table', 'figure', 'chart', 'text', 'header', 'footer',
                            'paragraph', 'heading1', 'heading2', 'list', 'index']]
        
        # 카테고리별 분류
        categories = {}
        for elem in visual_elements:
            cat = elem.get('category', 'unknown')
            categories[cat] = categories.get(cat, 0) + 1
        
        print(f"발견된 시각적 요소:")
        for cat, count in categories.items():
            print(f"  - {cat}: {count}개")
        print(f"  - 총합: {len(visual_elements)}개")
        
        if not visual_elements:
            print("시각적 요소를 찾을 수 없습니다.")
            return []
        
        results = []
        
        with pymupdf.open(self.pdf_file) as doc:
            for idx, element in enumerate(visual_elements, 1):
                category = element.get('category', 'unknown')
                coords = element.get('bounding_box', [])
                
                # ✅ 텍스트 계열은 실제 텍스트 저장
                text_categories = ['text', 'header', 'footer', 
                                   'paragraph', 'heading1', 'heading2', 
                                   'list', 'index']
                if category in text_categories:
                    text_content = element.get("text", "").strip()
                    if text_content:
                        results.append({"type": "text", "category": category, "content": text_content})
                        print(f"저장됨 [텍스트-{category}]: {text_content[:30]}...")
                    continue

                # ✅ 표는 Markdown 테이블로 변환 시도 + 이미지도 같이 저장
                if category == "table":
                    table_text = element.get("text", "").strip()
                    if table_text:
                        rows = [row.strip() for row in table_text.split("\n") if row.strip()]
                        md_table = []
                        for i, row in enumerate(rows):
                            cells = [c for c in row.split() if c]
                            md_row = "| " + " | ".join(cells) + " |"
                            md_table.append(md_row)
                            if i == 0:
                                md_table.append("| " + " | ".join(["---"] * len(cells)) + " |")
                        if md_table:
                            results.append({"type": "table", "category": "table", "markdown": "\n".join(md_table)})
                            print(f"저장됨 [표-텍스트]: {rows[0][:30]}...")
                    # 표도 이미지 추출 계속 진행 (아래 로직 수행)

                # 나머지 (table / figure / chart)는 기존 로직 그대로
                if not coords:
                    continue
                
                json_page = element.get('page', 1)
                actual_page = start_page + json_page - 1 - 1  # -1 for 0-based indexing
                if actual_page >= len(doc):
                    continue
                
                page = doc[actual_page]
                
                pix = page.get_pixmap(dpi=300)
                img = Image.frombytes("RGB", [pix.width, pix.height], pix.samples)
                img_w, img_h = img.size
                
                meta_w, meta_h = meta_pages.get(json_page, (page.rect.width, page.rect.height))
                scale_x = img_w / meta_w
                scale_y = img_h / meta_h
                
                xs = [c['x'] for c in coords]
                ys = [c['y'] for c in coords]
                x1, x2 = min(xs), max(xs)
                y1, y2 = min(ys), max(ys)
                
                left = int(x1 * scale_x)
                top = int(y1 * scale_y)
                right = int(x2 * scale_x)
                bottom = int(y2 * scale_y)
                
                if category == 'table':
                    padding = 40
                elif category in ['figure', 'chart']:
                    padding = 30
                else:
                    padding = 25
                
                crop_left = max(0, left - padding)
                crop_top = max(0, top - padding)
                crop_right = min(img_w, right + padding)
                crop_bottom = min(img_h, bottom + padding)
                
                if left < 100:
                    crop_left = max(0, left - padding * 1.5)
                if top < 100:
                    crop_top = max(0, top - padding * 1.5)
                if right > img_w - 100:
                    crop_right = min(img_w, right + padding * 1.5)
                if bottom > img_h - 100:
                    crop_bottom = min(img_h, bottom + padding * 1.5)
                
                crop_box = (int(crop_left), int(crop_top), int(crop_right), int(crop_bottom))
                if crop_box[2] <= crop_box[0] or crop_box[3] <= crop_box[1]:
                    continue
                
                cropped_img = img.crop(crop_box)
                base_name = os.path.splitext(os.path.basename(json_file))[0]
                output_file = os.path.join(output_dir, f"{base_name}_{category}_{idx}.png")
                cropped_img.save(output_file)
                
                # 디버그 이미지
                debug_img = img.copy()
                draw = ImageDraw.Draw(debug_img)
                colors = {'table': 'blue', 'figure': 'green', 'chart': 'orange'}
                color = colors.get(category, 'red')
                draw.rectangle([left, top, right, bottom], outline=color, width=2)
                draw.rectangle(crop_box, outline="red", width=3)
                draw.text((crop_box[0], crop_box[1] - 30), f"{category.upper()} {idx}", fill="red")
                debug_file = os.path.join(output_dir, f"{base_name}_{category}_{idx}_debug.png")
                debug_img.save(debug_file)
                
                results.append({"type": "image", "category": category, "path": output_file})
                print(f"저장됨 [{category}]: {output_file}")
        
        print(f"\n=== 추출 완료 ===")
        print(f"총 {len(results)}개 요소 추출 완료 (텍스트+이미지+표)")
        return results


# 실행 코드 (상대경로 + URL 인코딩 적용, 표 이미지는 제외)
if __name__ == "__main__":
    print("표 + 그래프 + 텍스트까지 추출하는 개선된 추출기 실행!")
    print("이미지 추출(그래프/차트만) + 텍스트 반영 + 표→Markdown 변환 + HTML/Markdown 생성")
    
    import glob
    import urllib.parse  # ✅ URL 인코딩용
    
    # 파일 경로 설정 /home/user/rag/split-pdf/(2차)2017년도 에너지사용량 통계_0230_0233.pdf
    original_pdf = "/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf"
    json_dir     = "/Users/ijongseung/Energy-RAG/rag/pdf"   # ← JSON 폴더 경로 # /home/user/rag/energy_statistic/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf
    output_dir   = "all_visuals_output"
    
    # 추출기 생성
    simple_extractor = SimpleWorkingExtractor(original_pdf)
    
    all_results = []
    # 폴더 안의 모든 JSON 파일 순회
    for json_path in sorted(glob.glob(os.path.join(json_dir, "*.json"))):
        print(f"\n▶ 처리중: {json_path}")
        simple_results = simple_extractor.extract_simple(json_path, output_dir)
        all_results.extend(simple_results)
    
    # Markdown 파일 생성
    md_file = os.path.join(output_dir, "all_results.md")
    with open(md_file, "w", encoding="utf-8") as f:
        f.write("# 📊 전체 추출 결과 (표 + 그래프 + 텍스트)\n\n")
        for item in all_results:
            if item["type"] == "image":
                # ✅ 표 이미지는 제외하고 그래프/차트만 넣기
                if item["category"] in ["figure", "chart"]:
                    rel_path = os.path.basename(item["path"])
                    rel_path_encoded = urllib.parse.quote(rel_path)
                    f.write(f"![{os.path.basename(item['path'])}]({rel_path_encoded})\n\n")
            elif item["type"] == "text":
                f.write(item["content"] + "\n\n")
            elif item["type"] == "table":
                f.write(item["markdown"] + "\n\n")
    
    # HTML 파일 생성
    html_file = os.path.join(output_dir, "all_results.html")
    with open(html_file, "w", encoding="utf-8") as f:
        f.write("<html><head><meta charset='utf-8'><title>전체 추출 결과</title></head><body>\n")
        f.write("<h1>📊 전체 추출 결과 (표 + 그래프 + 텍스트)</h1>\n")
        for item in all_results:
            if item["type"] == "image":
                if item["category"] in ["figure", "chart"]:  # ✅ 표 이미지 제외
                    rel_path = os.path.relpath(item["path"], output_dir)
                    rel_path_encoded = urllib.parse.quote(rel_path)
                    f.write(f"<div style='margin:20px 0;'><img src='{rel_path_encoded}' "
                            f"alt='{os.path.basename(item['path'])}' "
                            f"style='max-width:100%; border:1px solid #ccc;'></div>\n")
            elif item["type"] == "text":
                text_content = item["content"].strip().replace("\n", "<br>")
                if len(text_content) <= 5 and text_content.startswith("-") and text_content.endswith("-"):
                    f.write(f"<div style='color:gray; font-size:0.9em; margin:10px 0;'>{text_content}</div>\n")
                else:
                    f.write(f"<p style='line-height:1.5; font-size:1.05em;'>{text_content}</p>\n")
            elif item["type"] == "table":
                f.write(f"<div style='margin:20px 0;'><pre>{item['markdown']}</pre></div>\n")
        f.write("</body></html>")
    
    print(f"\n✅ 완료! 총 {len(all_results)}개 요소 추출됨 (텍스트 + 표[Markdown] + 그래프/차트[이미지])")
    print(f"📄 Markdown 파일: {md_file}")
    print(f"🌐 HTML 파일: {html_file}")

표 + 그래프 + 텍스트까지 추출하는 개선된 추출기 실행!
이미지 추출(그래프/차트만) + 텍스트 반영 + 표→Markdown 변환 + HTML/Markdown 생성

▶ 처리중: /Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009.json
발견된 시각적 요소:
  - figure: 2개
  - paragraph: 6개
  - heading1: 10개
  - list: 6개
  - index: 3개
  - 총합: 27개
저장됨 [figure]: all_visuals_output/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009_figure_1.png
저장됨 [텍스트-paragraph]: 승인(협의)번호
제337003호...
저장됨 [텍스트-heading1]: 2024 산업부문 (대상년도 : 2023)
에너지사용 ...
저장됨 [텍스트-heading1]: Industry Sector Energy and GHG...
저장됨 [텍스트-heading1]: 2024 Industry Sector Energy
GH...
저장됨 [텍스트-paragraph]: ECO...
저장됨 [figure]: all_visuals_output/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009_figure_7.png
저장됨 [텍스트-paragraph]: 산업통상자원부...
저장됨 [텍스트-paragraph]: 한국에너지공단
KOREA ENERGY AGENCY...
저장됨 [텍스트-heading1]: 2024년 산업부문
에너지 사용 및 온실가스 배출량 통...
저장됨 [텍스트-heading1]: - 광업·제조업 -
'23년 실적자료...
저장됨 [텍스트-heading1]: 2024. 12....
저장됨 [텍스트-heading1]: 일 러 두 기...
저장됨 [텍스트-list]: ○ 본 보고서는 산업부문 에너지 사용 및 온실가스 배출...
저장됨 [텍스트-list]: ○ 202

## 랭그래프를 이용한 코드 

In [37]:
from typing import TypedDict

class GraphState(TypedDict):
    filepath: str
    filetype: str
    page_numbers: list[int]
    batch_size: int
    split_filepaths: list[str]
    analyzed_files: list[str]
    page_elements: dict[int, dict[str, list[dict]]]
    page_metadata: dict[int, dict]
    page_summary: dict[int, str]
    images: dict[int, list[dict]]           # figure, chart만
    images_summary: dict[int, list[dict]]   # figure, chart 해석만
    tables: dict[int, list[dict]]           # 통합: 마크다운 + 이미지 + 해석
    texts: dict[int, list[dict]]
    texts_summary: dict[int, dict]


# 변수 지정
# 실제 state 초기화
state: GraphState = {
    "filepath": "/Users/ijongseung/Energy-RAG/rag/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf",
    "filetype": "pdf", # 파일형태를 채우는 함수
    "page_numbers": [], # 페이지 번호를 채우는 함수
    "batch_size": 4,
    "split_filepaths": [], # 
    "analyzed_files": [], #  extract_page_elements에서 부여
    "page_elements": {},  # extract_page_elements의 return 값에서 제공
    "page_metadata": {}, # page_metadata() ㅎ함수
    "page_summary": {}, # 아직 구현 x
    "images": [], # crop_image_and_table
    "images_summary": [], # create_image_summary_data_batches
    "tables": [], # crop_image_and_table
    "tables_summary": {}, # create_image_summary_data_batches
    "texts": {}, # crop_image_and_table
    "texts_summary": {} # create_image_summary_data_batches
}

In [38]:
state

{'filepath': '/Users/ijongseung/Energy-RAG/rag/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf',
 'filetype': 'pdf',
 'page_numbers': [],
 'batch_size': 4,
 'split_filepaths': [],
 'analyzed_files': [],
 'page_elements': {},
 'page_metadata': {},
 'page_summary': {},
 'images': [],
 'images_summary': [],
 'tables': [],
 'tables_summary': {},
 'texts': {},
 'texts_summary': {}}

In [39]:
## 문서를 배치 단위로 추출
def split_pdf(state: GraphState):
    """
    입력 PDF를 여러 개의 작은 PDF 파일로 분할합니다.
    :param state: GraphState 객체, PDF 파일 경로와 배치 크기 정보를 포함
    :return: 분할된 PDF 파일 경로 목록을 포함한 GraphState 객체
    """
    filepath = state["filepath"]
    batch_size = state["batch_size"]

    input_pdf = pymupdf.open(filepath)
    num_pages = len(input_pdf)
    print(f"총 페이지 수: {num_pages}")

    ret = []
    for start_page in range(0, num_pages, batch_size):
        end_page = min(start_page + batch_size, num_pages) - 1

        input_file_basename = os.path.splitext(filepath)[0]
        output_file = f"{input_file_basename}_{start_page:04d}_{end_page:04d}.pdf"
        print(f"분할 PDF 생성: {output_file}")

        with pymupdf.open() as output_pdf:
            output_pdf.insert_pdf(input_pdf, from_page=start_page, to_page=end_page)
            output_pdf.save(output_file)
            ret.append(output_file)

    input_pdf.close()
    return GraphState(split_filepaths=ret)

In [40]:
# 이 부분 변경이 필요함.
def extract_page_metadata(state: GraphState) -> GraphState:
    """
    PDF 페이지의 크기(width, height)를 추출하여 state["page_metadata"]에 저장합니다.
    
    :param state: GraphState 객체 (filepath 포함)
    :return: page_metadata가 추가된 GraphState
    """
    filepath = "/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf"
    doc = pymupdf.open(filepath)
    metadata = {}

    for i, page in enumerate(doc, start=1):
        rect = page.rect
        metadata[i] = {
            "size": [int(rect.width), int(rect.height)]
        }
    doc.close()

    state["page_metadata"] = metadata
    return state


In [41]:
state_out = extract_page_metadata(state)
state.update(state_out)
state["page_metadata"] # 왼쪽 키는 page 번호, 옆은 valye

{1: {'size': [595, 841]},
 2: {'size': [595, 841]},
 3: {'size': [595, 841]},
 4: {'size': [595, 841]},
 5: {'size': [595, 841]},
 6: {'size': [595, 841]},
 7: {'size': [595, 841]},
 8: {'size': [595, 841]},
 9: {'size': [595, 841]},
 10: {'size': [595, 841]},
 11: {'size': [595, 841]},
 12: {'size': [595, 841]},
 13: {'size': [595, 841]},
 14: {'size': [595, 841]},
 15: {'size': [595, 841]},
 16: {'size': [595, 841]},
 17: {'size': [595, 841]},
 18: {'size': [595, 841]},
 19: {'size': [595, 841]},
 20: {'size': [595, 841]},
 21: {'size': [595, 841]},
 22: {'size': [595, 841]},
 23: {'size': [595, 841]},
 24: {'size': [595, 842]},
 25: {'size': [595, 842]},
 26: {'size': [595, 842]},
 27: {'size': [595, 842]},
 28: {'size': [595, 842]},
 29: {'size': [595, 842]},
 30: {'size': [595, 842]},
 31: {'size': [595, 842]},
 32: {'size': [595, 841]},
 33: {'size': [595, 841]},
 34: {'size': [595, 841]},
 35: {'size': [595, 841]},
 36: {'size': [595, 841]},
 37: {'size': [595, 841]},
 38: {'siz

In [57]:
state

{'filepath': '/Users/ijongseung/Energy-RAG/rag/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf',
 'filetype': 'pdf',
 'page_numbers': [],
 'batch_size': 4,
 'split_filepaths': [],
 'analyzed_files': ['/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0010_0019.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0020_0029.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0030_0039.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0040_0049.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0050_0059.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0060_0069.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0070_0079.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0080_0089.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실

In [58]:
import os

def extract_start_end_page(filename: str):
    """
    파일명에 포함된 '_0000_0009' 같은 패턴에서 시작/끝 페이지 추출
    :param filename: JSON 또는 PDF 파일 경로
    :return: (start_page, end_page) 튜플 (int)
    """
    # 파일명만 추출
    basename = os.path.splitext(os.path.basename(filename))[0]
    
    # 언더스코어(_) 기준으로 분리
    parts = basename.split("_")
    
    try:
        # 뒤에서 두 개가 start, end 페이지 번호
        start = int(parts[-2])
        end = int(parts[-1])
    except Exception:
        start, end = 0, 0  # 실패 시 기본값
    
    return start, end

In [59]:
import glob
import os

def extract_page_elements(state: GraphState):
    # JSON 파일 폴더 지정 (PDF가 있는 폴더 기반으로)
    ## 이 위치 반영하여 처리 : /home/user/rag/energy_statistic/2024산업부문에너지온실가스실태조사및통계분석보고서_0170_0179.json
    json_dir = "/Users/ijongseung/Energy-RAG/rag/pdf"

    print(json_dir)
    
    # 폴더 안의 모든 JSON 파일 탐색
    json_files = sorted(glob.glob(os.path.join(json_dir, "*.json")))
    state["analyzed_files"] = json_files

    page_elements = dict()
    element_id = 0

    for json_file in json_files:
        start_page, _ = extract_start_end_page(json_file)

        with open(json_file, "r", encoding="utf-8") as f:
            data = json.load(f)

        for element in data["elements"]:
            original_page = int(element["page"])
            relative_page = start_page + original_page - 1

            if relative_page not in page_elements:
                page_elements[relative_page] = []

            element["id"] = element_id
            element_id += 1
            element["page"] = relative_page

            page_elements[relative_page].append(element)

    return GraphState(page_elements=page_elements, analyzed_files=json_files)


In [60]:
state_out = extract_page_elements(state)
state.update(state_out)
state["page_elements"] # 왼쪽 키는 page 번호, 옆은 valye

/Users/ijongseung/Energy-RAG/rag/pdf


{0: [{'bounding_box': [{'x': 67, 'y': 67},
    {'x': 192, 'y': 67},
    {'x': 192, 'y': 191},
    {'x': 67, 'y': 191}],
   'category': 'figure',
   'html': '<figure id=\'0\'><img style=\'font-size:14px\' alt="가 통\n국 계\nNATION AL STA TISTICS" data-coord="top-left:(67,67); bottom-right:(192,191)" /></figure>',
   'id': 0,
   'page': 0,
   'text': '가 통\n국 계\nNATION AL STA TISTICS'},
  {'bounding_box': [{'x': 79, 'y': 192},
    {'x': 180, 'y': 192},
    {'x': 180, 'y': 233},
    {'x': 79, 'y': 233}],
   'category': 'paragraph',
   'html': "<br><p id='1' data-category='paragraph' style='font-size:16px'>승인(협의)번호<br>제337003호</p>",
   'id': 1,
   'page': 0,
   'text': '승인(협의)번호\n제337003호'},
  {'bounding_box': [{'x': 102, 'y': 299},
    {'x': 923, 'y': 299},
    {'x': 923, 'y': 432},
    {'x': 102, 'y': 432}],
   'category': 'heading1',
   'html': "<h1 id='2' style='font-size:22px'>2024 산업부문 (대상년도 : 2023)<br>에너지사용 및 온실가스 배출량 통계</h1>",
   'id': 2,
   'page': 0,
   'text': '2024 산업부문 (대상년도 : 2023

In [61]:
state

{'filepath': '/Users/ijongseung/Energy-RAG/rag/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf',
 'filetype': 'pdf',
 'page_numbers': [],
 'batch_size': 4,
 'split_filepaths': [],
 'analyzed_files': ['/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0000_0009.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0010_0019.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0020_0029.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0030_0039.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0040_0049.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0050_0059.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0060_0069.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0070_0079.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서_0080_0089.json',
  '/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실

In [62]:
state.keys()


dict_keys(['filepath', 'filetype', 'page_numbers', 'batch_size', 'split_filepaths', 'analyzed_files', 'page_elements', 'page_metadata', 'page_summary', 'images', 'images_summary', 'tables', 'tables_summary', 'texts', 'texts_summary'])

In [63]:
def extract_tag_elements_per_page(state: GraphState) -> GraphState:
    """
    page_elements를 이미지, 표, 텍스트로 분류
    """
    page_elements = state["page_elements"]
    parsed_page_elements = {}

    for key, page_element in page_elements.items():
        image_elements = []
        table_elements = []
        text_elements = []

        for element in page_element:
            if element["category"] in ["figure", "chart"]:
                image_elements.append(element)
            elif element["category"] == "table":
                table_elements.append(element)
            else:
                text_elements.append(element)

        parsed_page_elements[key] = {
            "image_elements": image_elements,
            "table_elements": table_elements,
            "text_elements": text_elements,
            "elements": page_element,  # 원본 포함
        }

    return GraphState(page_elements=parsed_page_elements)

In [64]:
state_out = extract_tag_elements_per_page(state)
state.update(state_out)

In [65]:
state["page_elements"] # 왼쪽 키는 page 번호, 옆은 valye

{0: {'image_elements': [{'bounding_box': [{'x': 67, 'y': 67},
     {'x': 192, 'y': 67},
     {'x': 192, 'y': 191},
     {'x': 67, 'y': 191}],
    'category': 'figure',
    'html': '<figure id=\'0\'><img style=\'font-size:14px\' alt="가 통\n국 계\nNATION AL STA TISTICS" data-coord="top-left:(67,67); bottom-right:(192,191)" /></figure>',
    'id': 0,
    'page': 0,
    'text': '가 통\n국 계\nNATION AL STA TISTICS'},
   {'bounding_box': [{'x': 1, 'y': 1177},
     {'x': 373, 'y': 1177},
     {'x': 373, 'y': 1626},
     {'x': 1, 'y': 1626}],
    'category': 'figure',
    'html': '<figure id=\'6\'><img alt="" data-coord="top-left:(1,1177); bottom-right:(373,1626)" /></figure>',
    'id': 6,
    'page': 0,
    'text': ''}],
  'table_elements': [],
  'text_elements': [{'bounding_box': [{'x': 79, 'y': 192},
     {'x': 180, 'y': 192},
     {'x': 180, 'y': 233},
     {'x': 79, 'y': 233}],
    'category': 'paragraph',
    'html': "<br><p id='1' data-category='paragraph' style='font-size:16px'>승인(협의)번호<br>

In [66]:
import os, json, pymupdf
from PIL import Image, ImageDraw

def crop_image_and_table(state: GraphState, output_dir="output_images", save_debug=True) -> GraphState:
    os.makedirs(output_dir, exist_ok=True)
    
    pdf_file = state["filepath"]
    json_files = state["analyzed_files"]
    
    images, tables, texts = {}, {}, {}
    
    with pymupdf.open(pdf_file) as doc:
        for json_file in json_files:
            with open(json_file, "r", encoding="utf-8") as f:
                data = json.load(f)
            
            # --- 메타데이터 (페이지 크기) ---
            meta_pages = {p.get("page"): (p.get("width"), p.get("height"))
                          for p in data.get("metadata", {}).get("pages", [])}

            filename = os.path.basename(json_file)
            if "_" in filename:
                parts = filename.replace(".json", "").split("_")
                try:
                    start_page = int(parts[-2]) + 1
                except:
                    start_page = 1
            else:
                start_page = 1
            
            for element in data.get("elements", []):
                category = element.get("category", "unknown")
                coords = element.get("bounding_box", [])
                page_num = int(element.get("page", 1))
                relative_page = start_page + page_num - 1
                element_id = element.get("id", "na")

                # -------------------------
                # 텍스트 저장
                # -------------------------
                if category in ["text", "header", "footer", "paragraph", 
                                "heading1", "heading2", "list", "index"]:
                    txt = element.get("text", "").strip()
                    if txt:
                        texts.setdefault(relative_page, []).append({
                            "page": relative_page,
                            "id": element_id,
                            "content": txt
                        })
                    continue

                # 좌표/페이지 유효성 검사
                if not coords or relative_page - 1 >= len(doc):
                    continue

                page = doc[relative_page - 1]
                pix = page.get_pixmap(dpi=300)
                img = Image.frombytes("RGB", [pix.width, pix.height], pix.samples)
                img_w, img_h = img.size

                meta_w, meta_h = meta_pages.get(page_num, (page.rect.width, page.rect.height))
                scale_x, scale_y = img_w / meta_w, img_h / meta_h

                xs = [c["x"] for c in coords]
                ys = [c["y"] for c in coords]
                left, right = int(min(xs) * scale_x), int(max(xs) * scale_x)
                top, bottom = int(min(ys) * scale_y), int(max(ys) * scale_y)

                crop_left, crop_top = max(0, left), max(0, top)
                crop_right, crop_bottom = min(img_w, right), min(img_h, bottom)

                if crop_right <= crop_left or crop_bottom <= crop_top:
                    continue

                fname = f"page{relative_page}_id{element_id}_{category}.png"
                fpath = os.path.join(output_dir, fname)

                cropped_img = img.crop((crop_left, crop_top, crop_right, crop_bottom))
                cropped_img.save(fpath)

                if save_debug:
                    debug_img = img.copy()
                    draw = ImageDraw.Draw(debug_img)
                    colors = {"table": "blue", "figure": "green", "chart": "orange"}
                    color = colors.get(category, "red")
                    draw.rectangle([left, top, right, bottom], outline=color, width=2)
                    draw.text((crop_left, max(0, crop_top - 20)), f"{category}-{element_id}", fill="red")
                    debug_path = os.path.join(output_dir, f"DEBUG_{fname}")
                    debug_img.save(debug_path)

                # -------------------------
                # 표 처리 (통합 구조)
                # -------------------------
                if category == "table":
                    table_text = element.get("text", "").strip()
                    md_table = ""
                    if table_text:
                        rows = [row.strip() for row in table_text.split("\n") if row.strip()]
                        md_table_list = []
                        for i, row in enumerate(rows):
                            cells = [c for c in row.split() if c]
                            md_row = "| " + " | ".join(cells) + " |"
                            md_table_list.append(md_row)
                            if i == 0:
                                md_table_list.append("| " + " | ".join(["---"] * len(cells)) + " |")
                        md_table = "\n".join(md_table_list)
                    
                    tables.setdefault(relative_page, []).append({
                        "page": relative_page,
                        "id": element_id,
                        "markdown": md_table,
                        "image_path": fpath,
                        "summary": None,      # 후처리 요약 예정
                        "category": "table"
                    })

                # -------------------------
                # 순수 이미지 처리 (figure, chart)
                # -------------------------
                elif category in ["figure", "chart"]:
                    images.setdefault(relative_page, []).append({
                        "page": relative_page,
                        "id": element_id,
                        "path": fpath,
                        "category": category
                    })
    
    return GraphState(images=images, tables=tables, texts=texts)

In [73]:
if __name__ == "__main__":
    pdf_file = "/Users/ijongseung/Energy-RAG/rag/pdf/2024산업부문에너지온실가스실태조사및통계분석보고서.pdf"
    json_dir = "/Users/ijongseung/Energy-RAG/rag/pdf"
    output_dir = "all_visuals_output"

    # 📌 state에 파일 경로 등록
    state["filepath"] = pdf_file

    # JSON 요소 추출
    state.update(extract_page_elements(state))
    state.update(extract_tag_elements_per_page(state))

    # 크롭 실행 (이미지 + 표 + 텍스트 + 디버그)
    state.update(crop_image_and_table(state, output_dir=output_dir, save_debug=True))

    print("\n=== 최종 GraphState 요약 ===")
    for page, imgs in state.get("images", {}).items():
        for p in imgs:
            print(f"page:{page}, path:{p}")
            
    print("표:", {k: len(v) for k, v in state.get("tables", {}).items()})
    print("텍스트:", {k: len(v) for k, v in state.get("texts", {}).items()})


/Users/ijongseung/Energy-RAG/rag/pdf

=== 최종 GraphState 요약 ===
page:1, path:{'page': 1, 'id': 0, 'path': 'all_visuals_output/page1_id0_figure.png', 'category': 'figure'}
page:1, path:{'page': 1, 'id': 6, 'path': 'all_visuals_output/page1_id6_figure.png', 'category': 'figure'}
page:20, path:{'page': 20, 'id': 25, 'path': 'all_visuals_output/page20_id25_chart.png', 'category': 'chart'}
page:20, path:{'page': 20, 'id': 27, 'path': 'all_visuals_output/page20_id27_figure.png', 'category': 'figure'}
page:20, path:{'page': 20, 'id': 35, 'path': 'all_visuals_output/page20_id35_chart.png', 'category': 'chart'}
page:21, path:{'page': 21, 'id': 2, 'path': 'all_visuals_output/page21_id2_figure.png', 'category': 'figure'}
page:21, path:{'page': 21, 'id': 17, 'path': 'all_visuals_output/page21_id17_figure.png', 'category': 'figure'}
page:22, path:{'page': 22, 'id': 20, 'path': 'all_visuals_output/page22_id20_figure.png', 'category': 'figure'}
page:22, path:{'page': 22, 'id': 21, 'path': 'all_visuals

In [74]:
# GPT API 사용해서 처리

from openai import OpenAI

client = OpenAI()  # 환경변수 OPENAI_API_KEY 필요

def create_text_summary(state: GraphState) -> GraphState:
    """
    GraphState에서 텍스트들을 모아서 페이지별 요약 생성
    GPT API 사용
    """
    texts = state["texts"]   # { page_num: [ {id, page, content}, ... ] }
    text_summary = {}

    # 페이지 번호 기준 정렬
    sorted_texts = sorted(texts.items(), key=lambda x: x[0])

    for page_num, elems in sorted_texts:
        page_text = "\n".join(e["content"] for e in elems if e.get("content"))
        if not page_text.strip():
            continue

        # GPT API에 요약 요청
        response = client.chat.completions.create(
            model="gpt-3.5-turbo", 
            messages=[
                {"role": "system", "content": "너는 전문적인 요약가다. 입력된 텍스트를 간결하고 명확하게 요약해라."},
                {"role": "user", "content": page_text}
            ],
            temperature=0.3,
            max_tokens=400
        )

        summary = response.choices[0].message.content.strip()

        # 메타데이터 포함
        text_summary[page_num] = {
            "page": page_num,
            "source_ids": [e["id"] for e in elems],   # 이 페이지의 텍스트 블록 id들
            "text_count": len(elems),                 # 텍스트 블록 개수
            "summary": summary
        }

    return GraphState(texts_summary=text_summary)

# 실행
state.update(create_text_summary(state))

In [75]:
state["texts_summary"]

{1: {'page': 1,
  'source_ids': [1, 2, 3, 4, 5, 7, 8],
  'text_count': 7,
  'summary': '2024년 산업부문 에너지 사용량과 온실가스 배출량 통계에 대한 제337003호 승인(협의)번호가 발급되었습니다. 해당 통계는 산업통상자원부와 한국에너지공단(KOREA ENERGY AGENCY)에서 제공됩니다.'},
 5: {'page': 5,
  'source_ids': [9, 10, 11],
  'text_count': 3,
  'summary': '2024년 광업 및 제조업 산업부문의 에너지 사용 및 온실가스 배출량 통계는 2023년 실적자료를 기준으로 한다.'},
 7: {'page': 7,
  'source_ids': [12, 13, 14, 15, 16, 17, 18],
  'text_count': 7,
  'summary': '2024년 산업부문 에너지 사용 및 온실가스 배출 현황 보고서는 기후변화 대응과 정책수립을 위한 자료로, 18만여 개 기업을 대상으로 조사를 실시했습니다. 보고서에서는 toe 환산, 온실가스 배출량 계산 방법 등을 설명하고 있으며, 통계표의 숫자는 반올림되어 일치하지 않을 수 있습니다. 문의는 한국에너지공단 통계분석실(052-920-0624)로 하면 됩니다.'},
 9: {'page': 9,
  'source_ids': [19, 20, 21, 22, 23, 24],
  'text_count': 6,
  'summary': '이 문서는 에너지 사용량과 온실가스 배출량 조사에 대한 요약이다. 조사의 법적 근거, 목적, 연혁, 주관기관, 조사 방법, 내용, 결과, 기대효과, 활용방안, 통계자료 신뢰성 확보 등에 대해 다루고 있다. 또한 용어 해설과 열량 환산, 온실가스 배출량 산정 기준, 그리고 분석항목에 대한 내용도 포함되어 있다.'},
 10: {'page': 10,
  'source_ids': [25, 26],
  'text_count': 2,
  'summary': '에

## ChatOllama 사용해서 처리

In [33]:
# chatollama 생성해서 처리

from langchain_community.chat_models import ChatOllama
from langchain_core.messages import HumanMessage, SystemMessage

def create_text_summary(state: dict) -> dict:
    """
    GraphState에서 텍스트들을 모아서 페이지별 요약 생성
    로컬 모델(ChatOllama, llama3.1:70b) 사용
    """
    texts = state["texts"]   # { page_num: [ {id, page, content}, ... ] }
    text_summary = {}

    # ChatOllama 초기화 (로컬 모델 연결)
    model = ChatOllama(
        model="llama3.1:70b",
        base_url="http://127.0.0.1:11434",  # ollama 서버 주소
        temperature=0.3
    )

    # 페이지 번호 기준 정렬
    sorted_texts = sorted(texts.items(), key=lambda x: x[0])

    for page_num, elems in sorted_texts:
        page_text = "\n".join(e["content"] for e in elems if e.get("content"))
        if not page_text.strip():
            continue

        # LLaMA 모델에 요약 요청
        response = model.invoke([
            SystemMessage(content="너는 전문적인 요약가다. 입력된 텍스트를 간결하고 명확하게 요약해라."),
            HumanMessage(content=page_text)
        ])

        summary = response.content.strip()

        # 메타데이터 포함
        text_summary[page_num] = {
            "page": page_num,
            "source_ids": [e["id"] for e in elems],   # 이 페이지의 텍스트 블록 id들
            "text_count": len(elems),                 # 텍스트 블록 개수
            "summary": summary
        }

    return {"text_summary": text_summary}

# 실행
state.update(create_text_summary(state))

##

In [76]:
import os
import base64
import time
import json
from openai import OpenAI

client = OpenAI()

# ---------------------------
# 파일명 파싱 (caption 제외)
# ---------------------------
def parse_filename(fname: str) -> dict | None:
    if not fname.lower().endswith(".png"):
        return None
    if "DEBUG" in fname.upper():
        return None
    if "caption" in fname.lower():   # caption 포함된 파일 제외
        return None

    try:
        base = fname.replace(".png", "")
        parts = base.split("_")   # ['page138', 'id38', 'table']
        page = int(parts[0].replace("page", ""))
        elem_id = int(parts[1].replace("id", ""))
        category = parts[2].lower() if len(parts) > 2 else "unknown"
        return {"page": page, "id": elem_id, "category": category}
    except Exception:
        return None


# ---------------------------
# 폴더 내 이미지 로드
# ---------------------------
def load_images_with_auto_meta(folder: str) -> list[dict]:
    images_meta = []
    for fname in os.listdir(folder):
        meta = parse_filename(fname)
        if meta is None:
            continue
        path = os.path.join(folder, fname)
        images_meta.append({
            "page": meta["page"],
            "id": meta["id"],
            "category": meta["category"],
            "path": path
        })
    return sorted(images_meta, key=lambda x: (x["page"], x["id"]))


# ---------------------------
# 이미지 요약 생성 (+ 체크포인트 & 스킵 기능)
# ---------------------------
def create_image_summary_data_batches(state: GraphState, folder: str,
                                      delay: float = 1.0,
                                      limit: int | None = None,
                                      checkpoint_file: str = "state_checkpoint.json") -> GraphState:
    images_meta = load_images_with_auto_meta(folder)
    summaries = []

    # 이미 처리된 UID 모음 (스킵 방지용)
    existing_uids = {s["uid"] for s in state.get("images_summary", [])}

    for idx, meta in enumerate(images_meta):
        if limit and idx >= limit:
            break

        page_num = meta["page"]
        uid = f"p{page_num}_id{meta['id']}"

        # 이미 처리된 경우 스킵
        if uid in existing_uids:
            print(f"⚠️ {uid} 이미 처리됨 → 스킵")
            continue

        text_context = state.get("text_summary", {}).get(page_num, "")
        img_path = meta["path"]

        with open(img_path, "rb") as f:
            img_base64 = base64.b64encode(f.read()).decode()

        try:
            response = client.chat.completions.create(
                model="gpt-4o-mini",
                messages=[
                    {"role": "system",
                     "content": (
                         "당신은 모두에게 존경을 받는 대단한 분석가입니다. "
                         "표 정보를 받는 경우 수치적인 부분을 확인하여 구체적으로 설명하세요. "
                         "그래프 정보를 받게 되면 그래프의 축과 수치, 트렌드를 구체적으로 설명하세요. "
                         "표, 그래프 둘 다 문맥이 주어지면 문맥과 함께 분석하세요."
                     )},
                    {
                        "role": "user",
                        "content": [
                            {"type": "text",
                             "text": f"페이지 {page_num}의 요약 텍스트:\n{text_context}\n\n"
                                     f"이 {meta['category']} 이미지를 문맥과 함께 해석해서 요약해 주세요."},
                            {"type": "image_url",
                             "image_url": {"url": f"data:image/png;base64,{img_base64}"}}
                        ]
                    }
                ],
                max_tokens=300, temperature=0.1
            )
        except Exception as e:
            print(f"❌ 오류 발생 (uid={uid}): {e}")
            break

        content = response.choices[0].message.content
        if isinstance(content, str):
            summary = content.strip()
        elif isinstance(content, list):
            summary = "".join([c["text"] for c in content if c["type"] == "text"]).strip()
        else:
            summary = ""

        summaries.append({
            "uid": uid,
            "page": page_num,
            "id": meta["id"],
            "category": meta["category"],
            "path": img_path,
            "summary": summary
        })

        print(f"✅ page {page_num}, id {meta['id']} ({meta['category']}) 요약 완료")

        # ---- 체크포인트 저장 ----
        state.setdefault("images_summary", []).append(summaries[-1])
        with open(checkpoint_file, "w", encoding="utf-8") as f:
            json.dump(state, f, ensure_ascii=False, indent=2)

        time.sleep(delay)

    return state


# ---------------------------
# 실행 예시
# ---------------------------
state.update(create_image_summary_data_batches(
    state, "all_visuals_output", delay=5, limit=0
))

print("📊 총 이미지:", len(load_images_with_auto_meta("all_visuals_output")))
print("📑 생성된 요약:", len(state.get("images_summary", [])))

if "images_summary" in state:
    for s in state["images_summary"]:
        print("➡️", s)

✅ page 1, id 0 (figure) 요약 완료
✅ page 1, id 6 (figure) 요약 완료
✅ page 20, id 25 (chart) 요약 완료
✅ page 20, id 27 (figure) 요약 완료
✅ page 20, id 34 (table) 요약 완료
✅ page 20, id 35 (chart) 요약 완료
✅ page 21, id 2 (figure) 요약 완료
✅ page 21, id 12 (table) 요약 완료
✅ page 21, id 17 (figure) 요약 완료
✅ page 22, id 20 (figure) 요약 완료
✅ page 22, id 21 (chart) 요약 완료
✅ page 22, id 23 (chart) 요약 완료
✅ page 22, id 25 (chart) 요약 완료
✅ page 23, id 31 (figure) 요약 완료
✅ page 24, id 38 (chart) 요약 완료
✅ page 24, id 41 (chart) 요약 완료
✅ page 24, id 45 (chart) 요약 완료
✅ page 24, id 47 (table) 요약 완료
✅ page 25, id 66 (figure) 요약 완료
✅ page 26, id 69 (chart) 요약 완료
✅ page 27, id 73 (chart) 요약 완료
✅ page 28, id 77 (figure) 요약 완료
✅ page 28, id 78 (figure) 요약 완료
✅ page 29, id 81 (figure) 요약 완료
✅ page 30, id 84 (figure) 요약 완료
✅ page 30, id 85 (figure) 요약 완료
✅ page 31, id 2 (figure) 요약 완료
✅ page 31, id 3 (figure) 요약 완료
✅ page 36, id 26 (table) 요약 완료
✅ page 36, id 28 (table) 요약 완료
✅ page 37, id 40 (table) 요약 완료
✅ page 38, id 49 (table) 요약 완료


In [77]:
state["images_summary"]

[{'uid': 'p1_id0',
  'page': 1,
  'id': 0,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id0_figure.png',
  'summary': '이 이미지는 "국가통계"라는 문구와 함께 통계 관련 기관의 로고로 보입니다. 로고 중앙에는 여러 개의 막대 그래프가 그려져 있으며, 이는 데이터와 통계의 시각화를 상징합니다. 색상은 주로 파란색과 녹색으로 구성되어 있어 신뢰성과 전문성을 나타냅니다. \n\n이러한 요소들은 국가 통계의 중요성과 데이터 기반 의사결정의 필요성을 강조하는 데 기여합니다. 로고는 통계 정보를 제공하는 기관의 정체성을 나타내며, 국민에게 신뢰할 수 있는 데이터를 제공하는 역할을 수행합니다.'},
 {'uid': 'p1_id6',
  'page': 1,
  'id': 6,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id6_figure.png',
  'summary': '이 이미지는 공장 아이콘과 함께 화살표가 오른쪽으로 향하고 있는 형태로, 산업 또는 제조 프로세스를 나타내는 것으로 보입니다. 화살표는 어떤 자원이나 정보가 공장으로 이동하고 있음을 시사하며, 이는 생산 과정이나 공급망의 흐름을 강조하는 요소로 해석될 수 있습니다. \n\n이러한 요소들은 산업의 효율성, 자원 관리, 또는 생산성 향상과 관련된 주제를 다루고 있을 가능성이 높습니다. 전체적으로, 이 이미지는 산업적 활동의 중요성과 그 흐름을 시각적으로 표현하고 있습니다.'},
 {'uid': 'p20_id25',
  'page': 20,
  'id': 25,
  'category': 'chart',
  'path': 'all_visuals_output/page20_id25_chart.png',
  'summary': '이 차트는 2019년부터 2023년까지의 에너지 사용량, 에너지 공급량, 그리고 온실가스 배출량을 보여줍니다

# 문제점
1. tables는 현재 마크다운으로 이루어져 있음.
2. table 그림을 보고 해석을 해야 하는게 맞음
3. 그러나 해석 정보는 images_summary안에 있는 상황
4. 근데 이미지 서머리는 category가 나눠져 있다... 이럼 어떻게 해야 하지?

In [34]:
state.keys() # table_summary가 image summary에 들어가 있는 상황임


dict_keys(['filepath', 'filetype', 'page_numbers', 'batch_size', 'split_filepaths', 'analyzed_files', 'page_elements', 'page_metadata', 'page_summary', 'images', 'images_summary', 'tables', 'tables_summary', 'texts', 'texts_summary'])

In [78]:
import json

with open("state_cache.json", "w", encoding="utf-8") as f:
    json.dump(state, f, ensure_ascii=False, indent=2)

print("✅ state 전체 저장 완료: state_cache.json")

✅ state 전체 저장 완료: state_cache.json


In [79]:
# key 확인
# images_summary에서 category별로 분리
tables_summary = [s for s in state["images_summary"] if s["category"] == "table"] # 이 친구가 tables_summary 를 대체하는 친구
images_summary = [s for s in state["images_summary"] if s["category"] in ["figure", "chart"]] # 이 친구가 images_summary 를 대체하는 친구

In [80]:
state.keys()

dict_keys(['filepath', 'filetype', 'page_numbers', 'batch_size', 'split_filepaths', 'analyzed_files', 'page_elements', 'page_metadata', 'page_summary', 'images', 'images_summary', 'tables', 'tables_summary', 'texts', 'texts_summary', 'pdf_file'])

In [81]:
# page summary 는 필요 없는듯함.
## 그럼 이제 그림, table이랑 연관지어서 설정하면 되는건데, 해당 정보는 images_summary
# state["page_summary"] 
state["images_summary"]

[{'uid': 'p1_id0',
  'page': 1,
  'id': 0,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id0_figure.png',
  'summary': '이 이미지는 "국가통계"라는 문구와 함께 통계 관련 기관의 로고로 보입니다. 로고 중앙에는 여러 개의 막대 그래프가 그려져 있으며, 이는 데이터와 통계의 시각화를 상징합니다. 색상은 주로 파란색과 녹색으로 구성되어 있어 신뢰성과 전문성을 나타냅니다. \n\n이러한 요소들은 국가 통계의 중요성과 데이터 기반 의사결정의 필요성을 강조하는 데 기여합니다. 로고는 통계 정보를 제공하는 기관의 정체성을 나타내며, 국민에게 신뢰할 수 있는 데이터를 제공하는 역할을 수행합니다.'},
 {'uid': 'p1_id6',
  'page': 1,
  'id': 6,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id6_figure.png',
  'summary': '이 이미지는 공장 아이콘과 함께 화살표가 오른쪽으로 향하고 있는 형태로, 산업 또는 제조 프로세스를 나타내는 것으로 보입니다. 화살표는 어떤 자원이나 정보가 공장으로 이동하고 있음을 시사하며, 이는 생산 과정이나 공급망의 흐름을 강조하는 요소로 해석될 수 있습니다. \n\n이러한 요소들은 산업의 효율성, 자원 관리, 또는 생산성 향상과 관련된 주제를 다루고 있을 가능성이 높습니다. 전체적으로, 이 이미지는 산업적 활동의 중요성과 그 흐름을 시각적으로 표현하고 있습니다.'},
 {'uid': 'p20_id25',
  'page': 20,
  'id': 25,
  'category': 'chart',
  'path': 'all_visuals_output/page20_id25_chart.png',
  'summary': '이 차트는 2019년부터 2023년까지의 에너지 사용량, 에너지 공급량, 그리고 온실가스 배출량을 보여줍니다

In [82]:
state["images_summary"]

[{'uid': 'p1_id0',
  'page': 1,
  'id': 0,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id0_figure.png',
  'summary': '이 이미지는 "국가통계"라는 문구와 함께 통계 관련 기관의 로고로 보입니다. 로고 중앙에는 여러 개의 막대 그래프가 그려져 있으며, 이는 데이터와 통계의 시각화를 상징합니다. 색상은 주로 파란색과 녹색으로 구성되어 있어 신뢰성과 전문성을 나타냅니다. \n\n이러한 요소들은 국가 통계의 중요성과 데이터 기반 의사결정의 필요성을 강조하는 데 기여합니다. 로고는 통계 정보를 제공하는 기관의 정체성을 나타내며, 국민에게 신뢰할 수 있는 데이터를 제공하는 역할을 수행합니다.'},
 {'uid': 'p1_id6',
  'page': 1,
  'id': 6,
  'category': 'figure',
  'path': 'all_visuals_output/page1_id6_figure.png',
  'summary': '이 이미지는 공장 아이콘과 함께 화살표가 오른쪽으로 향하고 있는 형태로, 산업 또는 제조 프로세스를 나타내는 것으로 보입니다. 화살표는 어떤 자원이나 정보가 공장으로 이동하고 있음을 시사하며, 이는 생산 과정이나 공급망의 흐름을 강조하는 요소로 해석될 수 있습니다. \n\n이러한 요소들은 산업의 효율성, 자원 관리, 또는 생산성 향상과 관련된 주제를 다루고 있을 가능성이 높습니다. 전체적으로, 이 이미지는 산업적 활동의 중요성과 그 흐름을 시각적으로 표현하고 있습니다.'},
 {'uid': 'p20_id25',
  'page': 20,
  'id': 25,
  'category': 'chart',
  'path': 'all_visuals_output/page20_id25_chart.png',
  'summary': '이 차트는 2019년부터 2023년까지의 에너지 사용량, 에너지 공급량, 그리고 온실가스 배출량을 보여줍니다

In [83]:
# 1. 데이터 구조 정리
def fix_table_structure(state):
    """현재 상태의 표 데이터 구조 정리"""
    
    # images_summary에서 표와 이미지 분리
    tables_from_images = [s for s in state["images_summary"] if s["category"] == "table"]
    pure_images = [s for s in state["images_summary"] if s["category"] in ["figure", "chart"]]
    
    # tables 데이터 보강
    enhanced_tables = {}
    
    for page, tables in state.get("tables", {}).items():
        enhanced_tables[page] = []
        
        for table in tables:
            # 해당 표의 해석 찾기
            for t_summary in tables_from_images:
                if t_summary["page"] == page and t_summary["id"] == table["id"]:
                    table["summary"] = t_summary["summary"]
                    table["image_path"] = t_summary["path"]
                    break
            
            enhanced_tables[page].append(table)
    
    # state 업데이트
    state["tables"] = enhanced_tables
    state["images_summary"] = pure_images  # 순수 이미지만 남김
    
    print(f"✅ 데이터 구조 정리 완료:")
    print(f"   - 순수 이미지: {len(pure_images)}개")
    print(f"   - 표 페이지: {len(enhanced_tables)}개")
    
    return state

# 2. 실행
state = fix_table_structure(state)

# 3. 확인
print("\n=== 정리된 구조 확인 ===")
print("images_summary 카테고리:", set(s["category"] for s in state["images_summary"]))

if state["tables"]:
    sample_page = list(state["tables"].keys())[0]
    sample_table = state["tables"][sample_page][0]
    print("표 데이터 구조:", list(sample_table.keys()))

✅ 데이터 구조 정리 완료:
   - 순수 이미지: 84개
   - 표 페이지: 153개

=== 정리된 구조 확인 ===
images_summary 카테고리: {'figure', 'chart'}
표 데이터 구조: ['page', 'id', 'markdown', 'image_path', 'summary', 'category']


In [69]:
state.keys()

dict_keys(['filepath', 'filetype', 'page_numbers', 'batch_size', 'split_filepaths', 'analyzed_files', 'page_elements', 'page_metadata', 'page_summary', 'images', 'images_summary', 'tables', 'tables_summary', 'texts', 'texts_summary'])

In [70]:
if state["tables"]:
    sample_page = list(state["tables"].keys())[0]
    sample_table = state["tables"][sample_page][0]
    print("표 데이터 구조:", list(sample_table.keys()))

표 데이터 구조: ['page', 'id', 'markdown', 'image_path', 'summary', 'category']


In [56]:
state.keys()

dict_keys(['filepath', 'filetype', 'page_numbers', 'batch_size', 'split_filepaths', 'analyzed_files', 'page_elements', 'page_metadata', 'page_summary', 'images', 'images_summary', 'tables', 'tables_summary', 'texts', 'texts_summary'])

In [84]:
# 현재 문제 - 여러개로 분리돼 있음 
# 이걸 합치는 방법을 찾아야 함.
state["tables"]
state["images_summary"]
state["texts_summary"]

{1: {'page': 1,
  'source_ids': [1, 2, 3, 4, 5, 7, 8],
  'text_count': 7,
  'summary': '2024년 산업부문 에너지 사용량과 온실가스 배출량 통계에 대한 제337003호 승인(협의)번호가 발급되었습니다. 해당 통계는 산업통상자원부와 한국에너지공단(KOREA ENERGY AGENCY)에서 제공됩니다.'},
 5: {'page': 5,
  'source_ids': [9, 10, 11],
  'text_count': 3,
  'summary': '2024년 광업 및 제조업 산업부문의 에너지 사용 및 온실가스 배출량 통계는 2023년 실적자료를 기준으로 한다.'},
 7: {'page': 7,
  'source_ids': [12, 13, 14, 15, 16, 17, 18],
  'text_count': 7,
  'summary': '2024년 산업부문 에너지 사용 및 온실가스 배출 현황 보고서는 기후변화 대응과 정책수립을 위한 자료로, 18만여 개 기업을 대상으로 조사를 실시했습니다. 보고서에서는 toe 환산, 온실가스 배출량 계산 방법 등을 설명하고 있으며, 통계표의 숫자는 반올림되어 일치하지 않을 수 있습니다. 문의는 한국에너지공단 통계분석실(052-920-0624)로 하면 됩니다.'},
 9: {'page': 9,
  'source_ids': [19, 20, 21, 22, 23, 24],
  'text_count': 6,
  'summary': '이 문서는 에너지 사용량과 온실가스 배출량 조사에 대한 요약이다. 조사의 법적 근거, 목적, 연혁, 주관기관, 조사 방법, 내용, 결과, 기대효과, 활용방안, 통계자료 신뢰성 확보 등에 대해 다루고 있다. 또한 용어 해설과 열량 환산, 온실가스 배출량 산정 기준, 그리고 분석항목에 대한 내용도 포함되어 있다.'},
 10: {'page': 10,
  'source_ids': [25, 26],
  'text_count': 2,
  'summary': '에

In [85]:
def integrate_table_data_properly(state):
    """
    images_summary의 표 해석을 tables에 통합하되, 
    images_summary에서는 제거하지 않음 (데이터 손실 방지)
    """
    
    # 1. images_summary에서 표 해석만 분류 (제거하지 않음!)
    table_interpretations = [s for s in state["images_summary"] if s["category"] == "table"]
    
    print(f"발견된 표 해석: {len(table_interpretations)}개")
    
    # 2. tables 데이터에 해석 추가
    enhanced_tables = {}
    
    for page, tables in state.get("tables", {}).items():
        enhanced_tables[page] = []
        
        for table in tables:
            enhanced_table = table.copy()  # 기존 데이터 복사
            
            # 해당 표의 해석 찾기
            for t_interp in table_interpretations:
                if (t_interp["page"] == page and t_interp["id"] == table["id"]):
                    enhanced_table["summary"] = t_interp["summary"]
                    enhanced_table["image_path"] = t_interp["path"]
                    enhanced_table["interpretation_uid"] = t_interp["uid"]
                    print(f"  ✅ 페이지 {page}, ID {table['id']} - 해석 연결됨")
                    break
            else:
                print(f"  ⚠️ 페이지 {page}, ID {table['id']} - 해석 못찾음")
            
            enhanced_tables[page].append(enhanced_table)
    
    # 3. state 업데이트 (images_summary는 그대로 유지!)
    state["tables"] = enhanced_tables
    
    print(f"✅ 표 데이터 통합 완료 (images_summary 보존)")
    return state

def create_comprehensive_rag_chunks(state):
    """
    모든 데이터를 포함한 완전한 RAG 청킹
    """
    chunks = []
    
    # 1. 텍스트 청크
    for page, texts in state["texts"].items():
        for text in texts:
            chunks.append({
                "content": text["content"],
                "metadata": {
                    "page": page,
                    "type": "text",
                    "id": text["id"],
                    "source": "texts"
                }
            })
    
    # 2. 텍스트 요약 청크
    for page, summary_data in state["texts_summary"].items():
        chunks.append({
            "content": summary_data["summary"],
            "metadata": {
                "page": page,
                "type": "text_summary",
                "source": "texts_summary"
            }
        })
    
    # 3. 🔥 통합된 표 청크 (마크다운 + 해석)
    table_count = 0
    for page, tables in state.get("tables", {}).items():
        for table in tables:
            content_parts = []
            
            if table.get("markdown"):
                content_parts.append(f"[표 구조]\n{table['markdown']}")
            
            if table.get("summary"):
                content_parts.append(f"[표 분석]\n{table['summary']}")
            
            if content_parts:
                content = "\n\n".join(content_parts)
                chunks.append({
                    "content": content,
                    "metadata": {
                        "page": page,
                        "type": "table_integrated",
                        "id": table["id"],
                        "image_path": table.get("image_path"),
                        "source": "tables_enhanced",
                        "has_markdown": bool(table.get("markdown")),
                        "has_analysis": bool(table.get("summary"))
                    }
                })
                table_count += 1
    
    # 4. 🔥 이미지 청크 (images_summary 전체 활용)
    image_count = 0
    table_only_count = 0
    
    for img_summary in state["images_summary"]:
        if img_summary["category"] == "table":
            # 표는 별도 처리했지만, 표 단독 해석도 포함
            content = f"[표 해석] {img_summary['summary']}"
            chunk_type = "table_analysis_only"
            table_only_count += 1
        else:
            # 순수 이미지 (figure, chart)
            content = f"[{img_summary['category'].upper()}] {img_summary['summary']}"
            chunk_type = "visual_analysis"
            image_count += 1
        
        chunks.append({
            "content": content,
            "metadata": {
                "page": img_summary["page"],
                "type": chunk_type,
                "category": img_summary["category"],
                "id": img_summary["id"],
                "uid": img_summary["uid"],
                "image_path": img_summary["path"],
                "source": "images_summary"
            }
        })
    
    print(f"✅ 청킹 완료:")
    print(f"   - 텍스트: {sum(1 for c in chunks if c['metadata']['type'] in ['text', 'text_summary'])}개")
    print(f"   - 통합표: {table_count}개")
    print(f"   - 표해석: {table_only_count}개") 
    print(f"   - 이미지: {image_count}개")
    print(f"   - 총합: {len(chunks)}개")
    
    return chunks

# 🔥 올바른 실행 순서
def build_proper_rag_system(state):
    """데이터 손실 없는 완전한 RAG 시스템"""
    
    print("🚀 완전한 RAG 시스템 구축 시작!")
    print("=" * 50)
    
    # 1. 표 데이터 통합 (images_summary 보존)
    state = integrate_table_data_properly(state)
    
    # 2. 포괄적 청킹
    chunks = create_comprehensive_rag_chunks(state)
    
    # 3. Vector DB 구축
    embeddings = []
    chunk_metadata = []
    
    print(f"\n📊 {len(chunks)}개 청크 임베딩 생성 중...")
    
    for i, chunk in enumerate(chunks):
        if i % 30 == 0:
            print(f"   진행률: {i}/{len(chunks)}")
            
        response = client.embeddings.create(
            model=EMBED_MODEL,
            input=chunk["content"]
        )
        
        embeddings.append(response.data[0].embedding)
        chunk_metadata.append({
            "content": chunk["content"],
            "metadata": chunk["metadata"]
        })
    
    # 4. FAISS 인덱스
    embeddings_array = np.array(embeddings, dtype=np.float32)
    faiss.normalize_L2(embeddings_array)
    
    index = faiss.IndexFlatIP(embeddings_array.shape[1])
    index.add(embeddings_array)
    
    # 5. 저장
    faiss.write_index(index, "complete_rag_db.faiss")
    
    with open("complete_rag_metadata.json", "w", encoding="utf-8") as f:
        json.dump(chunk_metadata, f, ensure_ascii=False, indent=2)
    
    print("=" * 50)
    print("🎉 완전한 RAG 시스템 구축 완료!")
    print(f"   - 파일: complete_rag_db.faiss")
    print(f"   - 메타데이터: complete_rag_metadata.json")
    
    return {
        "index": index,
        "metadata": chunk_metadata,
        "chunks": chunks
    }

In [77]:
# 올바른 방식으로 실행
rag_result = build_proper_rag_system(state)

# 검색 테스트
def search_complete_db(query: str, k: int = 5):
    index = faiss.read_index("complete_rag_db.faiss")
    
    with open("complete_rag_metadata.json", "r", encoding="utf-8") as f:
        metadata = json.load(f)
    
    response = client.embeddings.create(model=EMBED_MODEL, input=query)
    query_embedding = np.array([response.data[0].embedding], dtype=np.float32)
    faiss.normalize_L2(query_embedding)
    
    scores, indices = index.search(query_embedding, k)
    
    results = []
    for score, idx in zip(scores[0], indices[0]):
        if idx < len(metadata):
            results.append({
                "content": metadata[idx]["content"],
                "metadata": metadata[idx]["metadata"],
                "similarity_score": float(score)
            })
    
    return results

# 테스트
results = search_complete_db("표 데이터 분석", k=3)
for r in results:
    print(f"타입: {r['metadata']['type']}, 페이지: {r['metadata']['page']}")
    print(f"내용: {r['content'][:100]}...")
    print("-" * 40)

🚀 완전한 RAG 시스템 구축 시작!
발견된 표 해석: 0개
  ⚠️ 페이지 20, ID 34 - 해석 못찾음
  ⚠️ 페이지 21, ID 12 - 해석 못찾음
  ⚠️ 페이지 24, ID 47 - 해석 못찾음
  ⚠️ 페이지 36, ID 26 - 해석 못찾음
  ⚠️ 페이지 36, ID 28 - 해석 못찾음
  ⚠️ 페이지 37, ID 40 - 해석 못찾음
  ⚠️ 페이지 38, ID 49 - 해석 못찾음
  ⚠️ 페이지 38, ID 53 - 해석 못찾음
  ⚠️ 페이지 39, ID 58 - 해석 못찾음
  ⚠️ 페이지 46, ID 42 - 해석 못찾음
  ⚠️ 페이지 47, ID 56 - 해석 못찾음
  ⚠️ 페이지 48, ID 64 - 해석 못찾음
  ⚠️ 페이지 49, ID 71 - 해석 못찾음
  ⚠️ 페이지 50, ID 81 - 해석 못찾음
  ⚠️ 페이지 55, ID 15 - 해석 못찾음
  ⚠️ 페이지 56, ID 23 - 해석 못찾음
  ⚠️ 페이지 57, ID 28 - 해석 못찾음
  ⚠️ 페이지 58, ID 35 - 해석 못찾음
  ⚠️ 페이지 61, ID 2 - 해석 못찾음
  ⚠️ 페이지 62, ID 8 - 해석 못찾음
  ⚠️ 페이지 64, ID 23 - 해석 못찾음
  ⚠️ 페이지 65, ID 28 - 해석 못찾음
  ⚠️ 페이지 68, ID 67 - 해석 못찾음
  ⚠️ 페이지 77, ID 67 - 해석 못찾음
  ⚠️ 페이지 78, ID 73 - 해석 못찾음
  ⚠️ 페이지 79, ID 77 - 해석 못찾음
  ⚠️ 페이지 80, ID 82 - 해석 못찾음
  ⚠️ 페이지 81, ID 2 - 해석 못찾음
  ⚠️ 페이지 82, ID 7 - 해석 못찾음
  ⚠️ 페이지 83, ID 11 - 해석 못찾음
  ⚠️ 페이지 84, ID 18 - 해석 못찾음
  ⚠️ 페이지 85, ID 22 - 해석 못찾음
  ⚠️ 페이지 89, ID 36 - 해석 못찾음
  ⚠️ 페이지 91, ID 5 - 해석 못찾음
  ⚠️ 페이지 92, ID 17 

KeyboardInterrupt: 

In [86]:
# 현재 상태 확인
def check_current_structure(state):
    """현재 데이터 구조가 올바른지 확인"""
    
    print("=== 현재 데이터 구조 확인 ===")
    
    # 1. tables 구조 확인
    tables_with_summary = 0
    tables_with_image = 0
    total_tables = 0
    
    for page, tables in state.get('tables', {}).items():
        for table in tables:
            total_tables += 1
            if table.get('summary'):
                tables_with_summary += 1
            if table.get('image_path'):
                tables_with_image += 1
    
    print(f"📊 Tables 현황:")
    print(f"   - 총 표: {total_tables}개")
    print(f"   - 해석 포함: {tables_with_summary}개")
    print(f"   - 이미지 포함: {tables_with_image}개")
    
    # 2. images_summary 확인
    images_summary = state.get('images_summary', [])
    categories = {}
    for item in images_summary:
        cat = item.get('category', 'unknown')
        categories[cat] = categories.get(cat, 0) + 1
    
    print(f"🖼️ Images Summary 현황:")
    print(f"   - 총 항목: {len(images_summary)}개")
    print(f"   - 카테고리: {categories}")
    
    # 3. 샘플 확인
    if total_tables > 0:
        sample_page = list(state['tables'].keys())[0]
        sample_table = state['tables'][sample_page][0]
        print(f"\n📋 표 샘플:")
        print(f"   - 페이지: {sample_table.get('page')}")
        print(f"   - ID: {sample_table.get('id')}")
        print(f"   - 마크다운 있음: {bool(sample_table.get('markdown'))}")
        print(f"   - 해석 있음: {bool(sample_table.get('summary'))}")
        print(f"   - 이미지 있음: {bool(sample_table.get('image_path'))}")
        
        if sample_table.get('summary'):
            print(f"   - 해석 샘플: {sample_table['summary'][:100]}...")
    
    return True

# 현재 구조 확인
check_current_structure(state)

# 🔥 이미 완벽한 구조이므로 바로 RAG 청킹 실행
def create_final_rag_chunks(state):
    """완성된 데이터 구조로 최종 RAG 청킹"""
    chunks = []
    
    # 1. 텍스트 청크
    text_count = 0
    for page, texts in state["texts"].items():
        for text in texts:
            chunks.append({
                "content": text["content"],
                "metadata": {
                    "page": page,
                    "type": "text",
                    "id": text["id"],
                    "source": "texts"
                }
            })
            text_count += 1
    
    # 2. 텍스트 요약 청크
    summary_count = 0
    for page, summary_data in state["texts_summary"].items():
        chunks.append({
            "content": summary_data["summary"],
            "metadata": {
                "page": page,
                "type": "text_summary",
                "source": "texts_summary"
            }
        })
        summary_count += 1
    
    # 3. 🔥 완성된 표 청크 (마크다운 + 해석)
    table_count = 0
    for page, tables in state["tables"].items():
        for table in tables:
            content_parts = []
            
            # 마크다운이 있으면 포함
            if table.get("markdown"):
                content_parts.append(f"[표 데이터]\n{table['markdown']}")
            
            # 해석이 있으면 포함
            if table.get("summary"):
                content_parts.append(f"[표 해석]\n{table['summary']}")
            
            # 내용이 있을 때만 청크 생성
            if content_parts:
                content = "\n\n".join(content_parts)
                chunks.append({
                    "content": content,
                    "metadata": {
                        "page": page,
                        "type": "table",
                        "id": table["id"],
                        "image_path": table.get("image_path"),
                        "source": "tables",
                        "has_markdown": bool(table.get("markdown")),
                        "has_summary": bool(table.get("summary")),
                        "has_image": bool(table.get("image_path"))
                    }
                })
                table_count += 1
    
    # 4. 🔥 이미지 청크 (figure, chart)
    image_count = 0
    for img_summary in state["images_summary"]:
        content = f"[{img_summary['category'].upper()}] {img_summary['summary']}"
        
        chunks.append({
            "content": content,
            "metadata": {
                "page": img_summary["page"],
                "type": "image",
                "category": img_summary["category"],
                "id": img_summary["id"],
                "uid": img_summary["uid"],
                "image_path": img_summary["path"],
                "source": "images_summary"
            }
        })
        image_count += 1
    
    print(f"✅ 최종 청킹 완료:")
    print(f"   - 텍스트: {text_count}개")
    print(f"   - 텍스트 요약: {summary_count}개")
    print(f"   - 표: {table_count}개")
    print(f"   - 이미지: {image_count}개")
    print(f"   - 총합: {len(chunks)}개")
    
    return chunks

# 🔥 최종 실행
chunks = create_final_rag_chunks(state)

# Vector DB 구축
def build_final_vector_db(chunks):
    """최종 Vector DB 구축"""
    
    embeddings = []
    chunk_metadata = []
    
    print(f"\n📊 {len(chunks)}개 청크 임베딩 생성 중...")
    
    for i, chunk in enumerate(chunks):
        if i % 50 == 0:
            print(f"   진행률: {i}/{len(chunks)}")
            
        response = client.embeddings.create(
            model=EMBED_MODEL,
            input=chunk["content"]
        )
        
        embeddings.append(response.data[0].embedding)
        chunk_metadata.append({
            "content": chunk["content"],
            "metadata": chunk["metadata"]
        })
    
    # FAISS 인덱스 생성
    embeddings_array = np.array(embeddings, dtype=np.float32)
    faiss.normalize_L2(embeddings_array)
    
    index = faiss.IndexFlatIP(embeddings_array.shape[1])
    index.add(embeddings_array)
    
    # 저장
    faiss.write_index(index, "final_rag_db.faiss")
    
    with open("final_rag_metadata.json", "w", encoding="utf-8") as f:
        json.dump(chunk_metadata, f, ensure_ascii=False, indent=2)
    
    print(f"🎉 Vector DB 구축 완료!")
    print(f"   - 파일: final_rag_db.faiss")
    print(f"   - 메타데이터: final_rag_metadata.json")
    print(f"   - 차원: {embeddings_array.shape[1]}")
    
    return index, chunk_metadata

# 실행
vector_index, metadata = build_final_vector_db(chunks)

=== 현재 데이터 구조 확인 ===
📊 Tables 현황:
   - 총 표: 180개
   - 해석 포함: 180개
   - 이미지 포함: 180개
🖼️ Images Summary 현황:
   - 총 항목: 84개
   - 카테고리: {'figure': 18, 'chart': 66}

📋 표 샘플:
   - 페이지: 20
   - ID: 34
   - 마크다운 있음: True
   - 해석 있음: True
   - 이미지 있음: True
   - 해석 샘플: 제공된 표는 다양한 산업 분야의 비율을 나타내고 있습니다. 각 항목은 특정 산업의 비율을 보여주며, 비율이 높은 순서로 나열되어 있습니다.

1. **비금속광물제품**: 4.9%로...
✅ 최종 청킹 완료:
   - 텍스트: 1387개
   - 텍스트 요약: 220개
   - 표: 180개
   - 이미지: 84개
   - 총합: 1871개

📊 1871개 청크 임베딩 생성 중...
   진행률: 0/1871
   진행률: 50/1871
   진행률: 100/1871
   진행률: 150/1871
   진행률: 200/1871
   진행률: 250/1871
   진행률: 300/1871
   진행률: 350/1871
   진행률: 400/1871
   진행률: 450/1871
   진행률: 500/1871
   진행률: 550/1871
   진행률: 600/1871
   진행률: 650/1871
   진행률: 700/1871
   진행률: 750/1871
   진행률: 800/1871
   진행률: 850/1871
   진행률: 900/1871
   진행률: 950/1871
   진행률: 1000/1871
   진행률: 1050/1871
   진행률: 1100/1871
   진행률: 1150/1871
   진행률: 1200/1871
   진행률: 1250/1871
   진행률: 1300/1871
   진행률: 1350/1871
   진행률: 1400/1871
   진행률: 1450/1871
   진행률:

## 이후 vectorDB 생성


In [88]:
# Vector DB 내용 진단
def diagnose_vector_db():
    """Vector DB에 어떤 타입의 데이터가 들어있는지 확인"""
    
    import json
    
    with open("/Users/ijongseung/Energy-RAG/rag/final_rag_metadata.json", "r", encoding="utf-8") as f:
        metadata = json.load(f)
    
    # 타입별 통계
    type_counts = {}
    category_counts = {}
    page_distribution = {}
    
    for item in metadata:
        meta = item["metadata"]
        
        # 타입별 카운트
        content_type = meta.get("type", "unknown")
        type_counts[content_type] = type_counts.get(content_type, 0) + 1
        
        # 카테고리별 카운트 (이미지/표의 경우)
        if "category" in meta:
            category = meta["category"]
            category_counts[category] = category_counts.get(category, 0) + 1
        
        # 페이지별 분포
        page = meta.get("page", 0)
        if page not in page_distribution:
            page_distribution[page] = {}
        page_distribution[page][content_type] = page_distribution[page].get(content_type, 0) + 1
    
    print("=== Vector DB 진단 결과 ===")
    print(f"총 청크 수: {len(metadata)}")
    print()
    
    print("📊 타입별 분포:")
    for type_name, count in sorted(type_counts.items()):
        print(f"   - {type_name}: {count}개")
    
    print("\n🖼️ 카테고리별 분포:")
    for category, count in sorted(category_counts.items()):
        print(f"   - {category}: {count}개")
    
    # 이미지 타입 상세 확인
    print("\n🔍 이미지 관련 청크 상세:")
    image_samples = []
    for item in metadata:
        meta = item["metadata"]
        if meta.get("type") == "image":
            image_samples.append({
                "page": meta["page"],
                "category": meta["category"],
                "content_preview": item["content"][:100]
            })
    
    for i, sample in enumerate(image_samples[:5], 1):
        print(f"   {i}. 페이지 {sample['page']} ({sample['category']}): {sample['content_preview']}...")
    
    if len(image_samples) > 5:
        print(f"   ... 외 {len(image_samples) - 5}개 더")
    
    return type_counts, category_counts, image_samples

# 진단 실행
type_counts, category_counts, image_samples = diagnose_vector_db()

# state["images_summary"] 재확인
print("\n=== state['images_summary'] 재확인 ===")
print(f"images_summary 총 개수: {len(state.get('images_summary', []))}")

categories_in_state = {}
for item in state.get('images_summary', []):
    cat = item.get('category', 'unknown')
    categories_in_state[cat] = categories_in_state.get(cat, 0) + 1

print("카테고리별 분포:")
for cat, count in categories_in_state.items():
    print(f"   - {cat}: {count}개")

# 샘플 확인
if state.get('images_summary'):
    sample = state['images_summary'][0]
    print(f"\n샘플 구조: {list(sample.keys())}")
    print(f"샘플 내용: {sample.get('summary', '')[:100]}...")

=== Vector DB 진단 결과 ===
총 청크 수: 1871

📊 타입별 분포:
   - image: 84개
   - table: 180개
   - text: 1387개
   - text_summary: 220개

🖼️ 카테고리별 분포:
   - chart: 66개
   - figure: 18개

🔍 이미지 관련 청크 상세:
   1. 페이지 1 (figure): [FIGURE] 이 이미지는 "국가통계"라는 문구와 함께 통계 관련 기관의 로고로 보입니다. 로고 중앙에는 여러 개의 막대 그래프가 그려져 있으며, 이는 데이터와 통계의 시각화를 ...
   2. 페이지 1 (figure): [FIGURE] 이 이미지는 공장 아이콘과 함께 화살표가 오른쪽으로 향하고 있는 형태로, 산업 또는 제조 프로세스를 나타내는 것으로 보입니다. 화살표는 어떤 자원이나 정보가 공장으...
   3. 페이지 20 (chart): [CHART] 이 차트는 2019년부터 2023년까지의 에너지 사용량, 에너지 공급량, 그리고 온실가스 배출량을 보여줍니다. 

1. **에너지 사용량**: 2019년 346,54...
   4. 페이지 20 (figure): [FIGURE] 이 이미지는 다양한 에너지원의 비율을 나타내고 있습니다. 각 에너지원의 점유율은 다음과 같습니다:

1. **석유류**: 48.1%로 가장 높은 비율을 차지하고 있...
   5. 페이지 20 (chart): [CHART] 이 차트는 한국의 각 지역별 에너지 사용량과 온실가스 배출량을 비교한 것입니다. 

- **에너지 사용량**은 청색 막대 그래프로 표시되며, 전남이 37,671.9천...
   ... 외 79개 더

=== state['images_summary'] 재확인 ===
images_summary 총 개수: 84
카테고리별 분포:
   - figure: 18개
   - chart: 66개

샘플 구조: ['uid', 'page', 'id', 'category', 'path', 'summary']
샘플 

## 이 부분부터 매우 핵심임

In [94]:
def search_final_db(query: str, k: int = 5):
    """final_rag_db.faiss를 사용한 검색 함수"""
    import faiss
    import json
    import numpy as np
    from openai import OpenAI
    
    # OpenAI 클라이언트 초기화
    client = OpenAI()
    EMBED_MODEL = "text-embedding-3-small"
    
    # FAISS 인덱스 로드
    index = faiss.read_index("final_rag_db.faiss")
    
    # 메타데이터 로드
    with open("final_rag_metadata.json", "r", encoding="utf-8") as f:
        metadata = json.load(f)
    
    # 쿼리 임베딩 생성
    response = client.embeddings.create(model=EMBED_MODEL, input=query)
    query_embedding = np.array([response.data[0].embedding], dtype=np.float32)
    faiss.normalize_L2(query_embedding)
    
    # 검색 수행
    scores, indices = index.search(query_embedding, k)
    
    # 결과 구성
    results = []
    for score, idx in zip(scores[0], indices[0]):
        if idx < len(metadata):  # 유효한 인덱스인지 확인
            results.append({
                "content": metadata[idx]["content"],
                "metadata": metadata[idx]["metadata"],
                "score": float(score)
            })
    
    return results

In [96]:
# 🎯 완전한 통합: 원본 텍스트 + 이미지 해석
def complete_integrated_search(question: str, k: int = 6):
    """원본 텍스트와 이미지 해석을 모두 포함한 완전한 검색"""
    
    # 1. 기본 검색으로 관련 페이지 찾기
    basic_results = search_final_db(question, k=15)
    relevant_pages = set()
    for result in basic_results[:8]:
        relevant_pages.add(result["metadata"]["page"])
    print(f"🔍 관련 페이지: {sorted(relevant_pages)}")
    
    
    # 2. 각 페이지의 모든 정보 수집
    complete_results = []
    
    for page in sorted(relevant_pages):
        page_content = []
        
        # 🔥 A. 원본 텍스트 요약 (있으면)
        if page in state.get("texts_summary", {}):
            summary = state["texts_summary"][page]["summary"]
            page_content.append(f"[페이지 {page} 텍스트 요약]\n{summary}")
        
        # 🔥 B. 핵심 텍스트 내용 (짧은 것들만)
        if page in state.get("texts", {}):
            for text in state["texts"][page][:3]:  # 최대 3개만
                if len(text["content"]) < 300:  # 짧은 텍스트만
                    page_content.append(f"[페이지 {page} 텍스트]\n{text['content']}")
        
        # 🔥 C. 이미지 해석
        page_images = [img for img in state["images_summary"] if img["page"] == page]
        for img in page_images:
            page_content.append(f"[페이지 {page} {img['category'].upper()} 분석]\n{img['summary']}")
        
        # 🔥 D. 표 데이터
        if page in state.get("tables", {}):
            for table in state["tables"][page]:
                table_parts = []
                if table.get("markdown"):
                    table_parts.append(f"표 데이터:\n{table['markdown']}")
                if table.get("summary"):
                    table_parts.append(f"표 해석:\n{table['summary']}")
                
                if table_parts:
                    page_content.append(f"[페이지 {page} 표 정보]\n" + "\n".join(table_parts))
        
        # 페이지별 통합 내용
        if page_content:
            integrated_content = f"=== 페이지 {page} 완전 정보 ===\n" + "\n\n".join(page_content)
            
            complete_results.append({
                "content": integrated_content,
                "metadata": {
                    "page": page,
                    "type": "complete_page",
                    "image_count": len(page_images),
                    "has_text_summary": page in state.get("texts_summary", {}),
                    "has_tables": page in state.get("tables", {})
                }
            })
    
    return complete_results[:k]

In [103]:
# 🔄 GPT-3.5로 변경한 완전한 RAG 시스템
def complete_rag_system_gpt(question: str, k: int = 5):
    """GPT-3.5를 사용한 완전 통합 RAG"""
    
    print(f"🔍 질문: {question}")
    print("=" * 80)
    
    # 1. 완전한 통합 검색 (기존과 동일)
    results = complete_integrated_search(question, k=k)
    
    # 2. 결과 분석
    total_images = sum(r["metadata"]["image_count"] for r in results)
    pages_with_text = sum(1 for r in results if r["metadata"]["has_text_summary"])
    pages_with_tables = sum(1 for r in results if r["metadata"]["has_tables"])
    
    print(f"📊 완전 통합 결과:")
    print(f"   - 페이지: {len(results)}개")
    print(f"   - 텍스트 요약 포함: {pages_with_text}개")
    print(f"   - 이미지 해석: {total_images}개")
    print(f"   - 표 데이터 포함: {pages_with_tables}개")
    print()
    
    for i, r in enumerate(results, 1):
        meta = r["metadata"]
        print(f"   📄 {i}. 페이지 {meta['page']} (텍스트:{'✓' if meta['has_text_summary'] else '✗'}, 이미지:{meta['image_count']}, 표:{'✓' if meta['has_tables'] else '✗'})")
    
    # 3. 컨텍스트 구성
    context = "\n\n".join([r["content"] for r in results])
    print(f"📝 전체 컨텍스트 길이: {len(context)} 글자")
    
    # 4. 🔥 GPT-3.5로 답변 생성
    print("🤖 GPT-3.5 답변 생성 중...")
    
    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",  # GPT-3.5 사용
            messages=[
                {
                    "role": "system", 
                    "content": """당신은 한국의 에너지 통계 전문 분석가입니다.

주어진 정보에는 다음이 포함되어 있습니다:
- 원본 텍스트 요약 및 내용
- 차트/그래프의 상세 해석
- 표 데이터 및 분석

답변 시 다음 사항을 준수하세요:
1. 원본 텍스트의 맥락과 차트 해석을 연결하여 설명
2. 구체적인 수치와 비율을 정확히 인용
3. 지역별 데이터는 지역명과 정확한 수치를 함께 제시
4. 여러 페이지의 정보를 종합하여 완전한 답변 제공
5. 어떤 페이지의 어떤 자료인지 명시

한국어로 전문적이고 상세하게 답변하세요. 없으면 없다고 말하세요."""
                },
                {
                    "role": "user", 
                    "content": f"""질문: {question}

완전 통합 참고자료 (원본 텍스트 + 차트 해석 + 표 데이터):
{context}

위 모든 정보를 종합하여 질문에 대해 완전하고 정확한 답변을 제공해주세요."""
                }
            ],
            temperature=0.0,
            max_tokens=1500
        )
        
        answer = response.choices[0].message.content
        
        print("🎯 GPT-3.5 완전 통합 답변:")
        print("-" * 50)
        print(answer)
        print("-" * 50)
        
        return {
            "answer": answer,
            "pages": len(results),
            "text_pages": pages_with_text,
            "images": total_images,
            "table_pages": pages_with_tables,
            "model": "gpt-3.5-turbo"
        }
        
    except Exception as e:
        print(f"❌ GPT-3.5 오류: {e}")
        return None

# 🔥 GPT-3.5로 테스트
print("=== GPT-3.5 완전 통합 RAG 시스템 테스트 ===")
result_gpt = complete_rag_system_gpt("지역별 산업단지별 온실가스 배출량")

=== GPT-3.5 완전 통합 RAG 시스템 테스트 ===
🔍 질문: 지역별 산업단지별 온실가스 배출량
🔍 관련 페이지: [29, 30, 31, 110, 160, 183]
📊 완전 통합 결과:
   - 페이지: 5개
   - 텍스트 요약 포함: 5개
   - 이미지 해석: 5개
   - 표 데이터 포함: 2개

   📄 1. 페이지 29 (텍스트:✓, 이미지:1, 표:✗)
   📄 2. 페이지 30 (텍스트:✓, 이미지:2, 표:✗)
   📄 3. 페이지 31 (텍스트:✓, 이미지:2, 표:✗)
   📄 4. 페이지 110 (텍스트:✓, 이미지:0, 표:✓)
   📄 5. 페이지 160 (텍스트:✓, 이미지:0, 표:✓)
📝 전체 컨텍스트 길이: 8547 글자
🤖 GPT-3.5 답변 생성 중...
🎯 GPT-3.5 완전 통합 답변:
--------------------------------------------------
산업부문에서의 지역별 온실가스 배출량과 에너지 사용량에 대한 정보를 종합하여 살펴보겠습니다.

1. **온실가스 배출량**:
   - **전남**은 2024년에 79,452.7톤 CO₂eq로 가장 큰 배출량을 기록했습니다. 이는 전체 배출량의 22.8%를 차지하며, 주요 산업은 제철금속산업, 화학, 정유입니다.
   - **충남**은 73,949.8톤 CO₂eq로 21.2%의 비율을 차지하며, 주요 산업은 제철금속산업, 화학, 정유입니다.
   - **울산**은 41,567.5톤 CO₂eq로 11.9%를 차지하며, 주요 산업은 화학, 정유, 제철금속산업입니다.
   - **경기**는 40,532.8톤 CO₂eq로 5위를 차지하며, 상위 지역들에 비해 상대적으로 낮은 배출량을 보입니다.

2. **에너지 사용량**:
   - **전남**은 37,421.9천 toe로 가장 높은 에너지 사용량을 기록했습니다. 이는 전체의 39.4%를 차지하며, 산업단지는 93개, 사업체는 3,409개입니다.
   - **울산**은 24,510.7천 toe로 두 

In [104]:
# graph.py
from langgraph.graph import StateGraph, END
from state import QAState
from nodes.router import node_router
from nodes.retriever import node_retriever
from nodes.integrated_retriever import node_integrated_retriever
from nodes.supervisor import node_supervisor
from nodes.text_agent import node_text_agent
from nodes.table_agent import node_table_agent
from nodes.reflection_agent import node_reflection_agent
from nodes.explainer import node_explainer

def _route(state: QAState):
    """에너지 산업 분석 라우팅 로직"""
    route = state.get("route", "text")
    return route

def build_graph():
    """에너지 산업 분석 전문 멀티에이전트 그래프 구성 (완전 통합 검색 포함)"""
    g = StateGraph(QAState)

    # 에너지 산업 분석 노드들 추가
    g.add_node("router", node_router)               # 쿼리 분석 및 연도 필터링
    g.add_node("retriever", node_retriever)         # 기본 문서 검색
    g.add_node("integrated_retriever", node_integrated_retriever)  # 🔥 완전 통합 검색
    g.add_node("supervisor", node_supervisor)       # 에너지 분석 라우팅
    g.add_node("energy_industry_agent", node_text_agent)       # 에너지산업분석전문가 (GPT-3.5 + 통합검색)
    g.add_node("renewable_energy_agent", node_table_agent)     # 재생에너지분석전문가 (신재생, ESG, 기술)
    g.add_node("reflection_agent", node_reflection_agent)  # 1회 성찰 및 개선
    g.add_node("explainer", node_explainer)         # 최종 결과 정리

    # 그래프 플로우 설정 (통합 검색 추가)
    g.set_entry_point("router")
    g.add_edge("router", "retriever")
    g.add_edge("retriever", "integrated_retriever")  # 🔥 기본 검색 후 통합 검색
    g.add_edge("integrated_retriever", "supervisor")
    
    # supervisor의 라우팅 결정에 따른 조건부 엣지
    g.add_conditional_edges(
        "supervisor", 
        _route, 
        {
            "text": "energy_industry_agent",         # 에너지산업분석전문가 (전통 에너지, 정책, 시장)
            "renewable": "renewable_energy_agent",   # 재생에너지분석전문가 (신재생, ESG, 기술)
            "done": "explainer"           # 분석 완료 시 바로 설명자로
        }
    )
    
    # 전문가 에이전트들이 성찰 단계로 이동
    g.add_edge("energy_industry_agent", "reflection_agent")      # 에너지산업분석전문가 → 성찰
    g.add_edge("renewable_energy_agent", "reflection_agent")     # 재생에너지분석전문가 → 성찰
    
    # 성찰 에이전트는 1회만 수행 후 supervisor로
    g.add_edge("reflection_agent", "supervisor")
    
    g.add_edge("explainer", END)

    return g.compile()


⚠️ NAS 연결 실패, 로컬 DB 사용


In [116]:
graph = build_graph()
print(graph.get_graph().draw_mermaid())


---
config:
  flowchart:
    curve: linear
---
graph TD;
	__start__([<p>__start__</p>]):::first
	router(router)
	retriever(retriever)
	integrated_retriever(integrated_retriever)
	supervisor(supervisor)
	energy_industry_agent(energy_industry_agent)
	renewable_energy_agent(renewable_energy_agent)
	reflection_agent(reflection_agent)
	explainer(explainer)
	__end__([<p>__end__</p>]):::last
	__start__ --> router;
	energy_industry_agent --> reflection_agent;
	integrated_retriever --> supervisor;
	reflection_agent --> supervisor;
	renewable_energy_agent --> reflection_agent;
	retriever --> integrated_retriever;
	router --> retriever;
	supervisor -. &nbsp;text&nbsp; .-> energy_industry_agent;
	supervisor -. &nbsp;done&nbsp; .-> explainer;
	supervisor -. &nbsp;renewable&nbsp; .-> renewable_energy_agent;
	explainer --> __end__;
	classDef default fill:#f2f0ff,line-height:1.2
	classDef first fill-opacity:0
	classDef last fill:#bfb6fc



## Postgre DB에 생성

In [155]:
# 기존 도커 컨테이너 상태 확인
import subprocess
import json

def check_docker_containers():
    """기존 도커 컨테이너 상태 확인"""
    
    print("=== 기존 도커 컨테이너 확인 ===")
    
    try:
        # 실행 중인 컨테이너 확인
        result = subprocess.run(['docker', 'ps', '--format', 'json'], 
                              capture_output=True, text=True)
        
        if result.returncode == 0:
            containers = []
            for line in result.stdout.strip().split('\n'):
                if line:
                    containers.append(json.loads(line))
            
            print(f"📊 실행 중인 컨테이너: {len(containers)}개")
            
            # PostgreSQL 관련 컨테이너 찾기
            postgres_containers = []
            for container in containers:
                name = container.get('Names', '')
                image = container.get('Image', '')
                if 'postgres' in image.lower() or 'pgvector' in image.lower():
                    postgres_containers.append(container)
            
            if postgres_containers:
                print("✅ PostgreSQL 컨테이너 발견:")
                for container in postgres_containers:
                    print(f"   📦 {container['Names']} - {container['Image']}")
                    print(f"   🚀 상태: {container['Status']}")
                    print(f"   �� 포트: {container['Ports']}")
            else:
                print("❌ PostgreSQL 컨테이너가 실행 중이지 않음")
                
            return postgres_containers
            
        else:
            print(f"❌ Docker 명령어 실행 실패: {result.stderr}")
            return []
            
    except Exception as e:
        print(f"❌ Docker 확인 오류: {e}")
        return []

# 실행
postgres_containers = check_docker_containers()

=== 기존 도커 컨테이너 확인 ===
📊 실행 중인 컨테이너: 2개
✅ PostgreSQL 컨테이너 발견:
   📦 rag-postgres_db1-1 - ankane/pgvector:latest
   🚀 상태: Up 8 days (healthy)
   �� 포트: 0.0.0.0:5432->5432/tcp, :::5432->5432/tcp


In [156]:
# 기존 도커 컨테이너 연결 정보 확인
def get_docker_connection_info(container_name=None):
    """도커 컨테이너 연결 정보 확인"""
    
    print("\n=== 도커 컨테이너 연결 정보 확인 ===")
    
    try:
        # 컨테이너 상세 정보 확인
        if container_name:
            result = subprocess.run(['docker', 'inspect', container_name], 
                                  capture_output=True, text=True)
        else:
            # 첫 번째 PostgreSQL 컨테이너 사용
            if postgres_containers:
                container_name = postgres_containers[0]['Names']
                result = subprocess.run(['docker', 'inspect', container_name], 
                                      capture_output=True, text=True)
            else:
                print("❌ PostgreSQL 컨테이너가 없습니다.")
                return None
        
        if result.returncode == 0:
            container_info = json.loads(result.stdout)[0]
            
            # 네트워크 설정 확인
            network_settings = container_info.get('NetworkSettings', {})
            ports = network_settings.get('Ports', {})
            
            print(f"📦 컨테이너: {container_name}")
            print(f"🖼️ 이미지: {container_info.get('Config', {}).get('Image', 'N/A')}")
            
            # 포트 매핑 확인
            print("🔗 포트 매핑:")
            for port, mapping in ports.items():
                if mapping:
                    print(f"   {port} -> {mapping[0]['HostPort']}")
            
            # 환경 변수 확인
            env_vars = container_info.get('Config', {}).get('Env', [])
            db_config = {}
            
            for env_var in env_vars:
                if 'POSTGRES' in env_var:
                    key, value = env_var.split('=', 1)
                    db_config[key] = value
                    print(f"   {key}: {value}")
            
            # 기본 연결 정보 구성
            connection_info = {
                'host': 'localhost',
                'port': '5432',  # 기본 포트
                'database': db_config.get('POSTGRES_DB', 'postgres'),
                'user': db_config.get('POSTGRES_USER', 'postgres'),
                'password': db_config.get('POSTGRES_PASSWORD', 'password')
            }
            
            # 포트 매핑이 있다면 실제 포트 사용
            if '5432/tcp' in ports and ports['5432/tcp']:
                connection_info['port'] = ports['5432/tcp'][0]['HostPort']
            
            print(f"\n🔌 연결 정보:")
            print(f"   호스트: {connection_info['host']}")
            print(f"   포트: {connection_info['port']}")
            print(f"   데이터베이스: {connection_info['database']}")
            print(f"   사용자: {connection_info['user']}")
            
            return connection_info
            
        else:
            print(f"❌ 컨테이너 정보 확인 실패: {result.stderr}")
            return None
            
    except Exception as e:
        print(f"❌ 연결 정보 확인 오류: {e}")
        return None

# 실행
docker_connection_info = get_docker_connection_info()


=== 도커 컨테이너 연결 정보 확인 ===
📦 컨테이너: rag-postgres_db1-1
🖼️ 이미지: ankane/pgvector:latest
🔗 포트 매핑:
   5432/tcp -> 5432
   POSTGRES_USER: zongseung
   POSTGRES_PASSWORD: 1234
   POSTGRES_DB: naver

🔌 연결 정보:
   호스트: localhost
   포트: 5432
   데이터베이스: naver
   사용자: zongseung


In [157]:
# 기존 도커 환경에 연결 테스트
def test_docker_connection(connection_info):
    """기존 도커 환경 연결 테스트"""
    
    print("\n=== 도커 환경 연결 테스트 ===")
    
    if not connection_info:
        print("❌ 연결 정보가 없습니다.")
        return None
    
    try:
        # 연결 문자열 생성
        connection_string = f"postgresql://{connection_info['user']}:{connection_info['password']}@{connection_info['host']}:{connection_info['port']}/{connection_info['database']}"
        
        # 엔진 생성
        engine = create_engine(connection_string)
        
        # 연결 테스트
        with engine.connect() as conn:
            # PostgreSQL 버전 확인
            result = conn.execute(text("SELECT version();"))
            version = result.fetchone()[0]
            print(f"✅ PostgreSQL 연결 성공: {version}")
            
            # PGVector 확장 확인
            result = conn.execute(text("SELECT * FROM pg_extension WHERE extname = 'vector';"))
            vector_ext = result.fetchone()
            
            if vector_ext:
                print("✅ PGVector 확장 설치됨")
            else:
                print("❌ PGVector 확장이 설치되지 않음")
                return None
            
            # 기존 테이블 확인
            result = conn.execute(text("""
                SELECT table_name 
                FROM information_schema.tables 
                WHERE table_schema = 'public' 
                AND table_name LIKE '%rag%' OR table_name LIKE '%chunk%';
            """))
            
            existing_tables = [row[0] for row in result.fetchall()]
            
            if existing_tables:
                print(f"📊 기존 RAG 관련 테이블: {existing_tables}")
            else:
                print("📊 기존 RAG 테이블 없음")
            
            return engine, existing_tables
            
    except Exception as e:
        print(f"❌ 연결 실패: {e}")
        return None, []

# 실행
if docker_connection_info:
    docker_engine, existing_tables = test_docker_connection(docker_connection_info)
else:
    print("❌ 도커 연결 정보가 없습니다.")


=== 도커 환경 연결 테스트 ===
✅ PostgreSQL 연결 성공: PostgreSQL 15.4 (Debian 15.4-2.pgdg120+1) on x86_64-pc-linux-gnu, compiled by gcc (Debian 12.2.0-14) 12.2.0, 64-bit
✅ PGVector 확장 설치됨
📊 기존 RAG 테이블 없음


In [162]:
# 현재 Vector DB 상태 확인
def check_existing_vector_db():
    """기존 Vector DB 상태 확인"""
    
    print("=== 기존 Vector DB 상태 확인 ===")
    
    # 1. 변수 확인
    print("1. 변수 상태:")
    if 'vector_index' in locals():
        print(f"   ✅ vector_index 존재")
        print(f"   �� 총 벡터 수: {vector_index.ntotal}")
        print(f"   📊 벡터 차원: {vector_index.d}")
    else:
        print("   ❌ vector_index 없음")
    
    if 'metadata' in locals():
        print(f"   ✅ metadata 존재")
        print(f"   📊 메타데이터 수: {len(metadata)}")
    else:
        print("   ❌ metadata 없음")
    
    # 2. 파일 확인
    print("\n2. 파일 상태:")
    import os
    
    faiss_file = "final_rag_db.faiss"
    metadata_file = "final_rag_metadata.json"
    
    if os.path.exists(faiss_file):
        file_size = os.path.getsize(faiss_file)
        print(f"   ✅ {faiss_file} 존재 ({file_size:,} bytes)")
    else:
        print(f"   ❌ {faiss_file} 없음")
    
    if os.path.exists(metadata_file):
        file_size = os.path.getsize(metadata_file)
        print(f"   ✅ {metadata_file} 존재 ({file_size:,} bytes)")
    else:
        print(f"   ❌ {metadata_file} 없음")
    
    # 3. 파일에서 로드 시도
    print("\n3. 파일에서 로드 시도:")
    try:
        if os.path.exists(faiss_file) and os.path.exists(metadata_file):
            # FAISS 인덱스 로드
            loaded_index = faiss.read_index(faiss_file)
            print(f"   ✅ FAISS 인덱스 로드 성공: {loaded_index.ntotal}개 벡터")
            
            # 메타데이터 로드
            with open(metadata_file, "r", encoding="utf-8") as f:
                loaded_metadata = json.load(f)
            print(f"   ✅ 메타데이터 로드 성공: {len(loaded_metadata)}개")
            
            return loaded_index, loaded_metadata
        else:
            print("   ❌ 파일이 없어서 로드할 수 없음")
            return None, None
            
    except Exception as e:
        print(f"   ❌ 로드 실패: {e}")
        return None, None

# 실행
vector_db, chunks_metadata = check_existing_vector_db()

=== 기존 Vector DB 상태 확인 ===
1. 변수 상태:
   ❌ vector_index 없음
   ❌ metadata 없음

2. 파일 상태:
   ✅ final_rag_db.faiss 존재 (11,489,325 bytes)
   ✅ final_rag_metadata.json 존재 (1,009,331 bytes)

3. 파일에서 로드 시도:
   ✅ FAISS 인덱스 로드 성공: 1870개 벡터
   ✅ 메타데이터 로드 성공: 1870개


In [163]:
# Vector DB에서 청크 데이터 재구성
def reconstruct_chunks_from_vector_db(vector_db, chunks_metadata):
    """Vector DB에서 청크 데이터 재구성"""
    
    print("\n=== Vector DB에서 청크 데이터 재구성 ===")
    
    if not vector_db or not chunks_metadata:
        print("❌ Vector DB 또는 메타데이터가 없습니다.")
        return None
    
    try:
        # 청크 데이터 재구성
        chunks_data = []
        
        for i, chunk_meta in enumerate(chunks_metadata):
            # 메타데이터에서 content 추출
            content = chunk_meta.get('content', '')
            chunks_data.append(content)
        
        print(f"📊 재구성된 청크 수: {len(chunks_data)}")
        
        # 샘플 확인
        if chunks_data:
            print(f"📄 첫 번째 청크 샘플: {chunks_data[0][:100]}...")
        
        return chunks_data
        
    except Exception as e:
        print(f"❌ 재구성 실패: {e}")
        return None

# 실행
if vector_db and chunks_metadata:
    chunks_data = reconstruct_chunks_from_vector_db(vector_db, chunks_metadata)
else:
    print("❌ Vector DB 데이터가 없습니다.")


=== Vector DB에서 청크 데이터 재구성 ===
📊 재구성된 청크 수: 1870
📄 첫 번째 청크 샘플: 승인(협의)번호
제337003호...


In [173]:
# 현재 Vector DB 상태 확인
def check_existing_vector_db():
    """기존 Vector DB 상태 확인"""
    
    print("=== 기존 Vector DB 상태 확인 ===")
    
    # 1. 변수 확인
    print("1. 변수 상태:")
    if 'vector_index' in locals():
        print(f"   ✅ vector_index 존재")
        print(f"   �� 총 벡터 수: {vector_index.ntotal}")
        print(f"   📊 벡터 차원: {vector_index.d}")
    else:
        print("   ❌ vector_index 없음")
    
    if 'metadata' in locals():
        print(f"   ✅ metadata 존재")
        print(f"   📊 메타데이터 수: {len(metadata)}")
    else:
        print("   ❌ metadata 없음")
    
    # 2. 파일 확인
    print("\n2. 파일 상태:")
    import os
    
    faiss_file = "final_rag_db.faiss"
    metadata_file = "final_rag_metadata.json"
    
    if os.path.exists(faiss_file):
        file_size = os.path.getsize(faiss_file)
        print(f"   ✅ {faiss_file} 존재 ({file_size:,} bytes)")
    else:
        print(f"   ❌ {faiss_file} 없음")
    
    if os.path.exists(metadata_file):
        file_size = os.path.getsize(metadata_file)
        print(f"   ✅ {metadata_file} 존재 ({file_size:,} bytes)")
    else:
        print(f"   ❌ {metadata_file} 없음")
    
    # 3. 파일에서 로드 시도
    print("\n3. 파일에서 로드 시도:")
    try:
        if os.path.exists(faiss_file) and os.path.exists(metadata_file):
            # FAISS 인덱스 로드
            loaded_index = faiss.read_index(faiss_file)
            print(f"   ✅ FAISS 인덱스 로드 성공: {loaded_index.ntotal}개 벡터")
            
            # 메타데이터 로드
            with open(metadata_file, "r", encoding="utf-8") as f:
                loaded_metadata = json.load(f)
            print(f"   ✅ 메타데이터 로드 성공: {len(loaded_metadata)}개")
            
            return loaded_index, loaded_metadata
        else:
            print("   ❌ 파일이 없어서 로드할 수 없음")
            return None, None
            
    except Exception as e:
        print(f"   ❌ 로드 실패: {e}")
        return None, None

# 실행
vector_db, chunks_metadata = check_existing_vector_db()

=== 기존 Vector DB 상태 확인 ===
1. 변수 상태:
   ❌ vector_index 없음
   ❌ metadata 없음

2. 파일 상태:
   ✅ final_rag_db.faiss 존재 (11,489,325 bytes)
   ✅ final_rag_metadata.json 존재 (1,009,331 bytes)

3. 파일에서 로드 시도:
   ✅ FAISS 인덱스 로드 성공: 1870개 벡터
   ✅ 메타데이터 로드 성공: 1870개


In [175]:
# Docker 컨테이너 연결 정보 확인
import subprocess
import json

def get_docker_connection_info():
    """Docker 컨테이너의 실제 연결 정보 확인"""
    
    print("=== Docker 컨테이너 연결 정보 확인 ===")
    
    try:
        # 실행 중인 컨테이너 확인
        result = subprocess.run(['docker', 'ps', '--format', 'json'], 
                              capture_output=True, text=True)
        
        if result.returncode == 0:
            containers = []
            for line in result.stdout.strip().split('\n'):
                if line:
                    containers.append(json.loads(line))
            
            # PostgreSQL 관련 컨테이너 찾기
            postgres_containers = []
            for container in containers:
                name = container.get('Names', '')
                image = container.get('Image', '')
                if 'postgres' in image.lower() or 'pgvector' in image.lower():
                    postgres_containers.append(container)
            
            if postgres_containers:
                print("✅ PostgreSQL 컨테이너 발견:")
                for container in postgres_containers:
                    print(f"   📦 {container['Names']} - {container['Image']}")
                    print(f"   �� 상태: {container['Status']}")
                    print(f"   포트: {container['Ports']}")
                    
                    # 컨테이너 상세 정보 확인
                    container_name = container['Names']
                    inspect_result = subprocess.run(['docker', 'inspect', container_name], 
                                                  capture_output=True, text=True)
                    
                    if inspect_result.returncode == 0:
                        container_info = json.loads(inspect_result.stdout)[0]
                        
                        # 환경 변수 확인
                        env_vars = container_info.get('Config', {}).get('Env', [])
                        db_config = {}
                        
                        for env_var in env_vars:
                            if 'POSTGRES' in env_var:
                                key, value = env_var.split('=', 1)
                                db_config[key] = value
                                print(f"      {key}: {value}")
                        
                        # 포트 매핑 확인
                        network_settings = container_info.get('NetworkSettings', {})
                        ports = network_settings.get('Ports', {})
                        
                        connection_info = {
                            'host': 'localhost',
                            'port': '5432',
                            'database': db_config.get('POSTGRES_DB', 'postgres'),
                            'user': db_config.get('POSTGRES_USER', 'postgres'),
                            'password': db_config.get('POSTGRES_PASSWORD', 'password')
                        }
                        
                        # 포트 매핑이 있다면 실제 포트 사용
                        if '5432/tcp' in ports and ports['5432/tcp']:
                            connection_info['port'] = ports['5432/tcp'][0]['HostPort']
                        
                        print(f"\n�� 연결 정보:")
                        print(f"   호스트: {connection_info['host']}")
                        print(f"   포트: {connection_info['port']}")
                        print(f"   데이터베이스: {connection_info['database']}")
                        print(f"   사용자: {connection_info['user']}")
                        print(f"   비밀번호: {connection_info['password']}")
                        
                        return connection_info
                        
            else:
                print("❌ PostgreSQL 컨테이너가 실행 중이지 않음")
                return None
                
        else:
            print(f"❌ Docker 명령어 실행 실패: {result.stderr}")
            return None
            
    except Exception as e:
        print(f"❌ Docker 확인 오류: {e}")
        return None

# 실행
docker_connection_info = get_docker_connection_info()

=== Docker 컨테이너 연결 정보 확인 ===
✅ PostgreSQL 컨테이너 발견:
   📦 rag-postgres_db1-1 - ankane/pgvector:latest
   �� 상태: Up 8 days (healthy)
   포트: 0.0.0.0:5432->5432/tcp, :::5432->5432/tcp
      POSTGRES_USER: zongseung
      POSTGRES_PASSWORD: 1234
      POSTGRES_DB: naver

�� 연결 정보:
   호스트: localhost
   포트: 5432
   데이터베이스: naver
   사용자: zongseung
   비밀번호: 1234


In [182]:
# 새로운 RAG 전용 데이터베이스 생성
def create_new_rag_database():
    """새로운 RAG 전용 데이터베이스 생성"""
    
    print("=== 새로운 RAG 데이터베이스 생성 ===")
    
    # 기본 연결 (postgres 데이터베이스로 연결)
    try:
        conn = psycopg2.connect(
            host='localhost',
            port=5432,
            database='postgres',  # 기본 postgres DB로 연결
            user='zongseung',
            password='1234'  # 실제 비밀번호로 변경
        )
        
        cursor = conn.cursor()
        
        # 새 데이터베이스 생성
        db_name = 'rag_vector_db'
        cursor.execute(f"CREATE DATABASE {db_name};")
        print(f"✅ 데이터베이스 '{db_name}' 생성 완료")
        
        # 연결 종료
        cursor.close()
        conn.close()
        
        return db_name
        
    except Exception as e:
        print(f"❌ 데이터베이스 생성 실패: {e}")
        return None

# 실행
new_db_name = create_new_rag_database()

=== 새로운 RAG 데이터베이스 생성 ===
❌ 데이터베이스 생성 실패: CREATE DATABASE cannot run inside a transaction block

